In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import os
import random
import operator
import pandas as pd
import numpy as np
import os
import pprint
from sklearn.metrics import mean_absolute_error as MAE
from sklearn.metrics import mean_squared_error as MSE
import pandasql as sqldf

Ziel dieses Notebooks ist es die Hyperparameter Lernrate und Epochenanzahl für das gegebene Neuronale Netz zu optimieren. Hierfür wird eine Klasse verwendet, die in gegebenen Intervallen verschiedene Kombinationen dieser Parameter geordnet ausprobiert (kein random search) und das beste Resultat, basierend auf übergebenen Trainingsdaten zurück gibt. 

In [2]:
def load_data(directory = 'sliced_data'):
    '''
        Funktion, die die aufbereiteten/vorbereiteten Daten aus existierenden CSV Dateien 
        einliest und je nach Vollständigkeit in zwei Dictionaries abspeichert,
        geschlüsselt nach der jeweiligen RaceId
    '''
    #Ids von Rennen, die als Regenrennen identifiziert wurden
    rain_id = [847,861,879,910,914,934,942,953,957,967,950,982]
    if os.path.exists(directory):
        csv_filenames = []
        #auslesen aller csv file dateinamen aus formula 1 datensatz und abspeichern in liste
        for filename in os.listdir(os.getcwd()+'/'+directory):
            typ = filename.split('.')[-1]
            name = filename.split('.')[0]
            if typ == 'csv':
                csv_filenames.append(filename)
        sliced_races = {}
        #einlesen und abspeichern als dataframe aller dateien
        for file in csv_filenames:
            try:
                df = pd.read_csv(directory+'/'+file, engine = 'python', sep = ';', decimal = '.')
                del df['Unnamed: 0']
            except Exception as e:
                df = pd.read_csv(directory+'/'+file, engine = 'c', sep = ';', decimal = '.')
                del df['Unnamed: 0']
                print(e)
            #print(df.head())
            f = int(file.split('_')[-1].split('.')[0])
            df["rain"] = 0
            #bias wird hinzugefügt
            #df['bias'] = 1
            #setzen der regenkomponente auf 1 für regenrennen
            if list(df["raceId"])[0] in rain_id:
                df["rain"] = 1
            sliced_races[f] = df
        print('Einlesen der sliced Dateien erfolgreich')
    else:
        raise ('sliced Dateien können nicht eingelesen werden, da kein entsprechendes Verzeichnis existiert!')
        
    if os.path.exists('split_data'):
        csv_filenames = []
        #auslesen aller csv file dateinamen aus formula 1 datensatz und abspeichern in liste
        for filename in os.listdir(os.getcwd()+'/split_data'):
            typ = filename.split('.')[-1]
            name = filename.split('.')[0]
            if typ == 'csv':
                csv_filenames.append(filename)
        split_by_race = {}
        #einlesen und abspeichern als dataframe aller dateien
        for file in csv_filenames:
            try:
                df = pd.read_csv('split_data/'+file, engine = 'python', sep = ';', decimal = '.')
                del df['Unnamed: 0']
            except Exception as e:
                df = pd.read_csv('split_data/'+file, engine = 'c', sep = ';', decimal = '.')
                del df['Unnamed: 0']
                print(e)
            f = int(file.split('_')[-1].split('.')[0])
            #hinzufügen eines bias
            #df['bias'] = 1
            split_by_race[f] = df
        print('Einlesen der split Dateien erfolgreich')
    else:
        raise('split Dateien können nicht eingelesen werden, da kein entsprechendes Verzeichnis existiert!')
        
    return sliced_races, split_by_race


def train_dev_test(data_dict, train_p = 0.7, dev_p = 0.2, test_p = 0.1, nogo_columns = []):
    
    if round(train_p+dev_p+test_p,1) !=1.0:
        raise ValueError ('No valid train/dev/test distribution')
    
    '''
        Daten werde in einem Dictionary übergeben, Dataframes werden in dieser 
        Funktion geshuffled und dann in einen Traindatensatz und in einen 
        Testdatensatz aufgeteilt.
    '''
    #aufteilen in train, dev, test counter
    train_count = round(len(data_dict.keys())*train_p, 0)
    dev_count = train_count+round(len(data_dict.keys())*dev_p,0)
    test_count = len(data_dict.keys())-(train_count+dev_count)
    
    #shufflen der übergebenen Daten
    keys = list(data_dict.keys())
    random.shuffle(keys)
    data_shuffled = {}
    for key in keys:
        data_shuffled[key] = data_dict[key]
        
    #erzeugen separater train,dev,test dictionaries
    train = {}
    dev = {}
    test = {}
    c = 0
    
    #daten sollen nicht in tensoren umgewandelt werden
    for id, df in data_shuffled.items():
        #entfernen nicht gewollter spalten aus dataframe
        cols = [col for col in df.columns if col not in nogo_columns]
        df = df[cols]
        if c < train_count:
            train[id] = df
        elif c >= train_count and c < dev_count:
            dev[id] = df
        else:
            test[id] = df
        c += 1
                
    return train, dev, test

def to_tensor(train_data, dev_data, test_data, nogo_columns = []):
    train = []
    train_ = {}
    dev = []
    dev_ = {}
    test = []
    test_ = {}
    
    for id, race in train_data.items():
        for did in race.driverId.unique():
            temp = race.where(race.driverId == did).dropna(how = "all")
            stop_sum = np.sum(temp['stop_binary'])#anzahl boxenstops
            temp['sum_milliseconds_pro_lap'] = temp['sum_milliseconds_pro_lap']/60000
            temp_y = list(temp["podium_position"])#list((temp["total_milliseconds"]/60000))
            #temp_y = temp_y[0]
            cols = [col for col in temp.columns if col not in nogo_columns]
            temp_x = temp[cols]
            #stops=temp_x.sum(axis = 0)[2] #Addierte anzahl an stops bis zu dem Zeitpunkt
            temp_x = temp_x.tail(1)
            temp_x['stop_binary'] = stop_sum
            x_tensor = torch.tensor(temp_x[cols].values)#torch.tensor(temp_x.values)
            #temp_x = x_tensor.float()
            train.append((x_tensor, [temp_y[0]]))
        train_[id] = train
        train = []
    for id, race in dev_data.items():
        for did in race.driverId.unique():
            temp = race.where(race.driverId == did).dropna(how = "all")
            stop_sum = np.sum(temp['stop_binary'])#anzahl boxenstops
            temp['sum_milliseconds_pro_lap'] = temp['sum_milliseconds_pro_lap']/60000
            temp_y = list(temp["podium_position"])#list((temp["total_milliseconds"]/60000))
            #temp_y = temp_y[0]
            cols = [col for col in temp.columns if col not in nogo_columns]
            temp_x = temp[cols]
            #stops=temp_x.sum(axis = 0)[2] #Addierte anzahl an stops bis zu dem Zeitpunkt
            temp_x = temp_x.tail(1)
            temp_x['stop_binary'] = stop_sum
            x_tensor = torch.tensor(temp_x[temp_x.columns].values)
            #temp_x = x_tensor.float()
            dev.append((x_tensor, [temp_y[0]]))
        dev_[id] = dev
        dev = []
    for id, race in test_data.items():
        for did in race.driverId.unique():
            temp = race.where(race.driverId == did).dropna(how = "all")
            stop_sum = np.sum(temp['stop_binary'])#anzahl boxenstops
            temp['sum_milliseconds_pro_lap'] = temp['sum_milliseconds_pro_lap']/60000
            temp_y = list(temp["podium_position"])#list((temp["total_milliseconds"]/60000))
            #temp_y = temp_y[0]
            cols = [col for col in temp.columns if col not in nogo_columns]
            temp_x = temp[cols]
            #stops=temp_x.sum(axis = 0)[2] #Addierte anzahl an stops bis zu dem Zeitpunkt
            temp_x = temp_x.tail(1)
            temp_x['stop_binary'] = stop_sum
            x_tensor = torch.tensor(temp_x[temp_x.columns].values)
            #temp_x = x_tensor.float()
            test.append((x_tensor, [temp_y[0]]))
        test_[id] = test
        test = []
        
    return train_,dev_,test_
        
#torch.tensor(df.values)
def train_test (data_dict, test_num = 5, nogo_columns = []):
    train_data = []
    test_data = []
    test_final = {}
    temp_y_podium = []
    test_races = list(data_dict.keys())
    random.shuffle(test_races)
    test_races = test_races[0:test_num]
    for key, value in data_dict.items():
        helper = key
        for did in value.driverId.unique():
            temp = value.where(value.driverId == did).dropna(how = "all")
            if list(temp["podium_position"])[0] < 0: #Top x finish positions
                pp = 1
            else:
                if key in test_races:
                    temp['sum_milliseconds_pro_lap'] = temp['sum_milliseconds_pro_lap']/60000
                    temp_y = list(temp["podium_position"])#list((temp["total_milliseconds"]/60000))
                    #temp_y = temp_y[0]
                    cols = [col for col in temp.columns if col not in nogo_columns]
                    temp_x = temp[cols]
                    stops=temp_x.sum(axis = 0)[2] #Addierte anzahl an stops bis zu dem Zeitpunkt
                    temp_x = temp_x.tail(1)
                    temp_x['stop_binary'] = stops
                    x_tensor = torch.tensor(temp_x[temp_x.columns].values)
                    #temp_x = x_tensor.float()
                    test_data.append((x_tensor, [temp_y[0]]))
                else:
                    temp['sum_milliseconds_pro_lap'] = temp['sum_milliseconds_pro_lap']/60000
                    temp_y = list(temp["podium_position"])#list((temp["total_milliseconds"]/60000))
                    #temp_y = temp_y[0]
                    cols = [col for col in temp.columns if col not in nogo_columns]
                    temp_x = temp[cols]
                    stops=temp_x.sum(axis = 0)[2] #Addierte anzahl an stops bis zu dem Zeitpunkt
                    temp_x = temp_x.tail(1)
                    temp_x['stop_binary'] = stops
                    x_tensor = torch.tensor(temp_x[temp_x.columns].values)
                    #temp_x = x_tensor.float()
                    train_data.append((x_tensor, [temp_y[0]]))
        if key in test_races:
            test_final[key]=test_data
        test_data = []
    random.shuffle(train_data)
    #random.shuffle(test_data)
    #test_data = train_data[len(train_data)-100:]
    train_data = train_data#[0:len(train_data)-100]
            
            #break
            #for i, row in temp.iterrows():
            
    return train_data, test_final

Einlesen der Dateien als Dataframes, welche in zwei Dictionaries gespeichert werden:<br>
- Attribut directory verweißt auf den Ordnernamen der sliced Dateien, Default ist 'sliced_data'
- für die split_by_race Daten sollte kein separates Directory angegeben werden müssen, da es keinen Unterschied zwischen den Rennen gibt! (Nur bei Slicing: Wie viele Prozent des Rennens möchte ich? ergibt ein anderes Directory Sinn)

In [8]:
sliced_races, split_by_race = load_data(directory = 'sliced_data50')
#temp_x = load_data(directory = 'sliced_data_50_neueForm')

Einlesen der sliced Dateien erfolgreich
Einlesen der split Dateien erfolgreich


In [9]:
columns =sliced_races[841].columns

In [10]:
columns

Index(['raceId', 'year', 'grandprix_name', 'lap_number', 'lap_position',
       'lap_in_milliseconds', 'driver_fullname', 'podium_position',
       'constructor_name', 'stop_binary',
       ...
       'constructorId_207.0', 'constructorId_208.0', 'constructorId_209.0',
       'constructorId_210.0', 'status_clean_DNF', 'status_clean_Finished',
       'status_clean_lapped', 'driverId', 'sum_milliseconds_pro_lap', 'rain'],
      dtype='object', length=121)

In [15]:
no_go=['year', 'podium_position', 'raceId','lap_number','total_laps','driverId',
                'grandprix_name', 'driver_fullname',
               'constructor_name', #'total_laps',
               #'status_clean', 'constructorId',
                'total_milliseconds',
               'lap_in_milliseconds', "status_clean", 'driverId']

nogo_columns = ['year', 'podium_position', 'raceId','lap_number','total_laps','driverId',
                'grandprix_name', 'driver_fullname',
               'constructor_name', #'total_laps',
               #'status_clean', 'constructorId',
                'total_milliseconds',
               'lap_in_milliseconds',
               'driverId_1.0',
                 'driverId_2.0',
                 'driverId_3.0',
                 'driverId_4.0',
                 'driverId_5.0',
                 'driverId_8.0',
                 'driverId_10.0',
                 'driverId_13.0',
                 'driverId_15.0',
                 'driverId_16.0',
                 'driverId_17.0',
                 'driverId_18.0',
                 'driverId_20.0',
                 'driverId_22.0',
                 'driverId_24.0',
                 'driverId_30.0',
                 'driverId_37.0',
                 'driverId_39.0',
                 'driverId_67.0',
                 'driverId_153.0',
                 'driverId_154.0',
                 'driverId_155.0',
                 'driverId_807.0',
                 'driverId_808.0',
                 'driverId_811.0',
                 'driverId_812.0',
                 'driverId_813.0',
                 'driverId_814.0',
                 'driverId_815.0',
                 'driverId_816.0',
                 'driverId_817.0',
                 'driverId_818.0',
                 'driverId_819.0',
                 'driverId_820.0',
                 'driverId_821.0',
                 'driverId_822.0',
                 'driverId_823.0',
                 'driverId_824.0',
                 'driverId_825.0',
                 'driverId_826.0',
                 'driverId_827.0',
                 'driverId_828.0',
                 'driverId_829.0',
                 'driverId_830.0',
                 'driverId_831.0',
                 'driverId_832.0',
                 'driverId_833.0',
                 'driverId_834.0',
                 'driverId_835.0',
                 'driverId_836.0',
                 'driverId_837.0',
                 'driverId_838.0',
                 'driverId_839.0',
                 'driverId_840.0',
                 'driverId_841.0',
                 'driverId_842.0',
                 'driverId_843.0',
                'driverId_1.0',
 'driverId_2.0',
 'driverId_3.0',
 'driverId_4.0',
 'driverId_5.0',
 'driverId_8.0',
 'driverId_10.0',
 'driverId_13.0',
 'driverId_15.0',
 'driverId_16.0',
 'driverId_17.0',
 'driverId_18.0',
 'driverId_20.0',
 'driverId_22.0',
 'driverId_24.0',
 'driverId_30.0',
 'driverId_37.0',
 'driverId_39.0',
 'driverId_67.0',
 'driverId_153.0',
 'driverId_154.0',
 'driverId_155.0',
 'driverId_807.0',
 'driverId_808.0',
 'driverId_811.0',
 'driverId_812.0',
 'driverId_813.0',
 'driverId_814.0',
 'driverId_815.0',
 'driverId_816.0',
 'driverId_817.0',
 'driverId_818.0',
 'driverId_819.0',
 'driverId_820.0',
 'driverId_821.0',
 'driverId_822.0',
 'driverId_823.0',
 'driverId_824.0',
 'driverId_825.0',
 'driverId_826.0',
 'driverId_827.0',
 'driverId_828.0',
 'driverId_829.0',
 'driverId_830.0',
 'driverId_831.0',
 'driverId_832.0',
 'driverId_833.0',
 'driverId_834.0',
 'driverId_835.0',
 'driverId_836.0',
 'driverId_837.0',
 'driverId_838.0',
 'driverId_839.0',
 'driverId_840.0',
 'driverId_841.0',
 'driverId_842.0',
 'driverId_843.0',
                   "status_clean"]

In [20]:
[c for c in columns if c not in nogo_columns]

['lap_position',
 'stop_binary',
 'race_completion',
 'grid',
 'form',
 'circuitId_1.0',
 'circuitId_2.0',
 'circuitId_3.0',
 'circuitId_4.0',
 'circuitId_5.0',
 'circuitId_6.0',
 'circuitId_7.0',
 'circuitId_9.0',
 'circuitId_10.0',
 'circuitId_11.0',
 'circuitId_12.0',
 'circuitId_13.0',
 'circuitId_14.0',
 'circuitId_15.0',
 'circuitId_17.0',
 'circuitId_18.0',
 'circuitId_20.0',
 'circuitId_22.0',
 'circuitId_24.0',
 'circuitId_32.0',
 'circuitId_35.0',
 'circuitId_68.0',
 'circuitId_69.0',
 'circuitId_70.0',
 'circuitId_71.0',
 'circuitId_73.0',
 'constructorId_1.0',
 'constructorId_3.0',
 'constructorId_4.0',
 'constructorId_5.0',
 'constructorId_6.0',
 'constructorId_9.0',
 'constructorId_10.0',
 'constructorId_15.0',
 'constructorId_131.0',
 'constructorId_164.0',
 'constructorId_166.0',
 'constructorId_205.0',
 'constructorId_206.0',
 'constructorId_207.0',
 'constructorId_208.0',
 'constructorId_209.0',
 'constructorId_210.0',
 'status_clean_DNF',
 'status_clean_Finished',
 '

Aufteilen des Datensatzes in einen Trainings-, einen Development- und einen Testteil mit Hilfe der Funktion train_dev_test(). Standardmäßig wird der Datensatz zu 70% in Trainings-, zu 20% in Dev- und zu 10% in Testdaten aufgeteilt. Die Verteilung kann mit den Parametern train_p,dev_p,test_p die der Funktion train_dev_test() übergeben werden können, angepasst werden. Wichtig ist bloß, dass insgesamt train_p,dev_p und test_p 1 ergeben. Die Datenbeispiele aus sliced_races werden vor dem Aufteilen geshuffled. Die Funktion train_dev_test() gibt die Datenbeispiele dann wieder in Dictionary Form zurück, wobei jeder RaceId ein DataFrame mit Renndaten zugeordnet wird. Im nächsten Schritt werden die drei Datensammlungen der Funktion to_tensor() übergeben, die nicht gewünschte Spalten aus den Datensätzen entfernt (nogo_columns) und diese dann in Tensoren abspeichert, die wiederrum  ihrem Targetvalue (podiums_position) zugeordnet werden, um die Überprüfung der Vorhersagen später zu vereinfachen. Tupel mit Datensatz und Targetvalue werden dann wieder in dem jeweiligen Dictionary abgespeichert und ihrer RaceId zugeordnet.

In [16]:
nogo_columns = ['year', 'podium_position', 'raceId','lap_number','total_laps','driverId',
                'grandprix_name', 'driver_fullname',
               'constructor_name', #'total_laps',
               #'status_clean', 'constructorId',
                'total_milliseconds',
               'lap_in_milliseconds',
               'driverId_1.0',
                 'driverId_2.0',
                 'driverId_3.0',
                 'driverId_4.0',
                 'driverId_5.0',
                 'driverId_8.0',
                 'driverId_10.0',
                 'driverId_13.0',
                 'driverId_15.0',
                 'driverId_16.0',
                 'driverId_17.0',
                 'driverId_18.0',
                 'driverId_20.0',
                 'driverId_22.0',
                 'driverId_24.0',
                 'driverId_30.0',
                 'driverId_37.0',
                 'driverId_39.0',
                 'driverId_67.0',
                 'driverId_153.0',
                 'driverId_154.0',
                 'driverId_155.0',
                 'driverId_807.0',
                 'driverId_808.0',
                 'driverId_811.0',
                 'driverId_812.0',
                 'driverId_813.0',
                 'driverId_814.0',
                 'driverId_815.0',
                 'driverId_816.0',
                 'driverId_817.0',
                 'driverId_818.0',
                 'driverId_819.0',
                 'driverId_820.0',
                 'driverId_821.0',
                 'driverId_822.0',
                 'driverId_823.0',
                 'driverId_824.0',
                 'driverId_825.0',
                 'driverId_826.0',
                 'driverId_827.0',
                 'driverId_828.0',
                 'driverId_829.0',
                 'driverId_830.0',
                 'driverId_831.0',
                 'driverId_832.0',
                 'driverId_833.0',
                 'driverId_834.0',
                 'driverId_835.0',
                 'driverId_836.0',
                 'driverId_837.0',
                 'driverId_838.0',
                 'driverId_839.0',
                 'driverId_840.0',
                 'driverId_841.0',
                 'driverId_842.0',
                 'driverId_843.0',
                   "status_clean"]
train, dev, test = train_dev_test(sliced_races)
train_T, dev_T, test_T = to_tensor(train, dev, test, nogo_columns)

In [5]:
print('Train:',len(train))
print('Dev:',len(dev))
print('Test:',len(test))
print('Rennen insgesamt:', len(train)+len(dev)+len(test))
print(25*'=')
print('Tensoren:')
print('Train:',len(train_T))
print('Dev:',len(dev_T))
print('Test:',len(test_T))
print('Rennen insgesamt:', len(train_T)+len(dev_T)+len(test_T))

Train: 96
Dev: 27
Test: 14
Rennen insgesamt: 137
Tensoren:
Train: 96
Dev: 27
Test: 14
Rennen insgesamt: 137


Definieren von notwendigen Klassen: 
    
Zuerst wird die Klasse für das Neuronale Netz definiert, danach die Klasse für die Optimierung der Hyperparameter Lernrate und Epochen Anzahl

In [41]:
class Netz(nn.Module):
    def __init__(self):
        super(Netz,self).__init__()
        #self.fc1 = nn.Linear(53, 150)
        self.fc1 = nn.Linear(10, 150)
        self.fc2 = nn.Linear(150, 180)
        self.fc3 = nn.Linear(180, 190)
        self.fc4 = nn.Linear(190, 120)
        self.fc5 = nn.Linear(120, 100)
        self.fc6 = nn.Linear(100, 70)
        self.fc7 = nn.Linear(70, 30)
        self.fc8 = nn.Linear(30, 1)
        self.dropout = nn.Dropout()
        
        
    def forward(self,x):
        x = self.fc1(x.float())
        x = F.relu(x.float())
        x = self.fc2(x.float())
        x = F.relu(x.float())
        x = self.dropout(x)
        x = self.fc3(x.float())
        x = F.relu(x.float())
        x = self.fc4(x.float())
        x = F.relu(x.float())
        #x = self.dropout(x)
        x = self.fc5(x.float())
        x = F.relu(x.float())
        x = self.fc6(x.float())
        x = F.relu(x.float())
        x = self.fc7(x.float())
        x = F.relu(x.float())
        x = self.fc8(x.float())
        return x
        

In [18]:
julian = {'first':['linear', 10,150],
         'relu0':['linear',150,180],
         'relu1':['dropout',0,0],
         'no_activation0':['linear',180,190],
         'relu2':['linear',190,120],
         'relu3':['linear',120,100],
         'relu4':['linear',100,70],
         'relu5':['linear',70,30],
         'relu6':['linear',30,1]}

In [42]:
class NetzDynamic(nn.Module):
    
    def __init__(self, layer_information):
        super(NetzDynamic,self).__init__()
        self.__layer_information = layer_information
        #definieren von einer Moduleliste, die die Layer enthalten wird
        self.layers = nn.ModuleList()
        
        #erzeugen der in layer_information übergebeben Layer und hinzufügen zu layers Moduleliste
        for specs in self.__layer_information.values():
            type_ = specs[0]
            in_ = specs[1]
            out_ = specs[2]
            if type_ == 'linear':
                self.layers.append(nn.Linear(in_,out_))
            if type_ == 'dropout':
                self.layers.append(nn.Dropout())
        
    def forward(self, x):
        #definieren eines dynamischen forward pass, activation function richtet sich nach dictionary key
        lay_idx = 0
        for activation, specs in self.__layer_information.items():
            
            if activation.startswith('relu'):
                layer = self.layers[lay_idx] #auswählen des relevanten Layers aus layers ModuleList
                if specs[0] == 'dropout':
                    x = F.relu(x.float())
                    x = layer(x)
                else:
                    x = F.relu(x.float())
                    x = layer(x.float())
                    
            if activation.startswith('sigmoid'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = torch.sigmoid(x.float())
                    x = layer(x)
                else:
                    x = torch.sigmoid(x.float())
                    x = layer(x.float())
                    
            if activation.startswith('tanh'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = torch.tanh(x.float())
                    x = layer(x)
                else:
                    x = torch.tanh(x.float())
                    x = layer(x.float())
                    
            #if activation.startswith('last'):
            #    layer = self.layers[lay_idx]
            #    if specs[0] == 'dropout':
            #        x = layer(x)
            #    else:
            #        x = layer(x.float()) 
            if activation.startswith("first"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float())
            if activation.startswith("no_activation"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float()) 
            lay_idx += 1
        
        return x

#### STOP

relu linear dropout linear --> in linear layer nach dropout keine activation!!!

**Baustelle**:
Es werden Netze zufällig erzeugt, mit jeweils einer festen Anzahl von Layern. Von diesen werden Variationen erzeugt. Ziel ist es zu sagen "alle Netze mit 5 Layern waren besser als alle Netze mit nur 4 Layern", um somit ein besseres Gefühl dafür zu bekommen, welche Layeranzahl am besten funktioniert. Außerdem werden die Netze mit einheitlichen Activation Funktionen erzeugt, sie haben also entweder nur ReLu, nur Tanh oder nur Sigmoid als Aktivierungsfunktion. Diese Netze sind direkt miteinander vergleichbar. Alle Netze haben ein Dropout Layer als drittes Layer.

#### WEITER 

In [43]:
class HP_Layer_Optimizer(object):
    
    def __init__ (self, 
                  layer_range = (2,8), #range mindestanzahl layer, max anzahl layer
                  input_start = 53, #anzahl inputneuronen für das Inputlayer
                  output_last = 1, #anzahl outputneuronen für das letzte layer
                  in_out_range = (30,200), #range in der sich die anzahl der Neuronen für die Hiddenlayer bewegen soll
                  random_activation = False,#boolean, die angibt ob activation functions random gepicked werden sollen
                  types = ['linear', 'dropout'],#layertypen, von denen gewählt wird
                  activations = ['relu', 'sigmoid', 'tanh'],#activation functions
                  activation_dist = [0.5,0.25,0.25],#wenn random_activation == False wird hier die Häufigkeit für jede Activation übergeben
                  dropout_num = 1,#anzahl von dropoutlayern pro NN
                  cuda = True,#soll mit cuda gearbeitet werden?
                  lr = 0.0001,#lernrate für adam optimizer
                  max_epochs = 5,#anzahl der Trainingsepochen
                  create_combinations = True, #sollen von der Klasse Netze erzeugt werden, oder sollen diese von außen in die Klasse gegeben werden?
                  create_variations = False,#soll von einer Layeranzahl mehr als ein Netz erzeugt werden?
                  num_variations = 4 #wenn Variationen erzeugt werden sollen wird eine festgelegte Zahl Netze mit 4 Layer, eine festgelegte Anzahl mit 5 Layern usw. erzeugt
                  ):
        
        self.__model = None #model, welches trainiert und getestet wird, wird hier zwischengespeichert
        self.__layer_range = layer_range #min und max anzahl von layern in Tupelform
        self.__input_start = input_start#Inputgröße für Startlayer/Inputlayer
        self.__output_last = output_last#Outputgröße für letztes Layer / Outputlayer
        self.__in_out_range = in_out_range#range in der sich die Anzahl der In- und Outputs für die Hiddenlayer bewegen soll (Tupelform)
        self.__layer_types = types#liste welche Layertypen enthält (bspw. linear oder dropout)
        self.__dropout_number = dropout_num#anzahl von layern, die pro Netz ein dropout Layer sein sollen
        self.__random_activation = random_activation#Boolean, ob die activation zufällig gewählt werden soll
        self.__create_variations = create_variations
        self.__number_of_variations = num_variations
        
        self.__combination_results = {}#dictionary, die dem schlüssel zu einer NN Kombi einen MAE zuordnet
        self.model_specs_combinations = {}#dictionary, welches die jeweiligen NN Kombinationen enthält (einem Schlüssel zugeordnet)
        self.train_data = None#trainingsdaten, die dem Optimizer übergeben werden für die Modelle
        self.test_data = None#developmentdaten, um die Modelle zu testen und Aussagen über die besten Kombinationen zu treffen
        self.lr = lr#lernrate für Modell OPtimizer (default Adam)
        self.max_epochs = max_epochs#Anzahl der Trainingsepochen
        self.cuda = cuda#Boolean, ob mit cuda gearbeitet werden soll oder nicht
        self.opt_combination = {}#dictionary enthält optimale kombination aus möglichen kombinationen
        
        self.__activations = None#entweder Liste (wenn activations random ausgewählt werden sollen), oder dictionary, 
        #wenn activation functions mit einer bestimmten Häufigkeit verwendet werden sollen
        if self.__random_activation:#random pick von activation functions
            self.__activations = activations
        else:#activation function sollen mit einer gewissen häufigkeit ausgewählt werden
            k = {}
            for a in range(len(types)):#zuordnen einer häufihkeit aus activation_dist liste zu jeder activation function aus types
                act = types[a]
                dist = activation_dist[a]
                k[act] = dist
            self.__activations = k
            
        #aufrufen der Funktion, die anhand der übergebenen Parameter Modellkombinationen erzeugt
        if create_combinations:
            self.__create_combinations()
        else:
            print('NN Kombinationen müssen in Dictionary Form selbst übergeben werden')
        
    def __train(self, epoch, optimizer):
        '''
            funktion übernimmt das Training von dem in self.__model
            zwischengespeicherten NN. 
            Epoch: Jetzige Epoche in der trainiert wird (für coolen print Befehl wichtig)
            Optimizer: Optimizer mit dem Parameter des NN aus self.__model optimiert werden
        '''
        if self.cuda:
            self.__model.cuda()
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0).cuda()
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    optimizer.zero_grad()
                    out = self.__model(data)
                    #print("Out: ", out, out.size())
                    #print("Target: ", target, target.size())
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                        epoch, batch_id *len(data), len(self.train_data),
                    100. * batch_id / len(self.train_data), loss.item()))
                    batch_id +=1
        else:
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    #data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)#.cuda()
                    shape = target.size()[1]
                    target = target.resize(shape,1)#.cuda()
                    optimizer.zero_grad()
                    out = self.__model(data)
                    #print("Out: ", out, out.size())
                    #print("Target: ", target, target.size())
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                        epoch, batch_id *len(data), len(self.train_data),
                    100. * batch_id / len(self.train_data), loss.item()))
                    batch_id +=1
            
    def __test(self):
        '''
            Funktion, die das Testen des Models aus self.__model auf den übergebenen Dev-Daten 
            (self.test_data) übernimmt und den gesamt MAE für das jeweilige Modell berechnet
        '''
        total = 0
        count = 0
        result_dict = {}
        result = pd.DataFrame(columns = ['target','prediction'])
        help_dict = {}
        if self.cuda:
            self.__model.cuda()
            for key in self.test_data.keys():
                #print(key)
                help_dict = {}
                for data, target in self.test_data[key]:
                    self.__model.eval()
                    #files.listdir(path)
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    out = self.__model(data).cpu()
                    #print(out)
                    out = out.detach().numpy()
                    #out = np.round(out)
                    target = target.cpu()
                    target = target.detach().numpy()
                    #print(data)
                    #print(data["driverId"])
                    total += abs(out - target[0][0])
                    #print("current_position: ", data[0][0].item())
                    #print("Output: ", out)
                    #print("Target: ", target)
                    help_dict[target[0][0]] = out
                    #print("Difference: ", out - target)
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                
                result = result.append(t, sort = True)
                
        else:
            for raceId in self.test_data.keys():
                #print(key)
                help_dict = {}
                for data, target in self.test_data[raceId]:
                    self.__model.eval()
                    #files.listdir(path)
                    #data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1)#.cuda()
                    out = self.__model(data)#.cpu()
                    #print(out)
                    out = out.detach().numpy()
                    #out = np.round(out)
                    #target = target.cpu()
                    target = target.detach().numpy()
                    #print(data)
                    #print(data["driverId"])
                    total += abs(out - target[0][0])
                    #print("current_position: ", data[0][0].item())
                    #print("Output: ", out)
                    #print("Target: ", target)
                    help_dict[target[0][0]] = out
                    #print("Difference: ", out - target)
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                result = result.append(t, sort = True)
        return result
    
    def get_all_information(self):
        
        print('All Model Combinations with encoding:\n', self.model_specs_combinations)
        print('Model Results:\n', self.__combination_results)
        print('Optimale Kombination:\n', self.opt_combination)
        
    def validate_combinations(self):
        
        for key, combination in self.model_specs_combinations.items():
            print(combination)
            self.__model = NetzDynamic(combination)
            optimizer = optim.Adam(self.__model.parameters(), lr = self.lr)
            #trainieren des modells
            for epoch in range(1,self.max_epochs):
                self.__train(epoch, optimizer)  
            
            result = self.__test()
            A = result.prediction.tolist()
            y = result.target.tolist()
            mae = MAE(A,y)
            
            
            
            self.__combination_results[key] = mae
            
        #finden der besten kombination nach minimalstem Error (MAE)
        key_min = min(self.__combination_results.keys(), key=(lambda k: self.__combination_results[k]))
        best_combination = self.model_specs_combinations[key_min]
        best_combination['mae'] = self.__combination_results[key_min]
        self.opt_combination = best_combination
        #self.__combination_overview[key] = specifics
        
        
    def __create_combinations(self):
        '''
            Funktion erzeugt Dictionarys, mit NN Modellspezifikationen, die
            später gegeneinander getestet werden sollen. Kombinationen werden
            in dem Dictionary self.model_specs_combinations unter einem 
            Schlüssel abgespeichert
        '''
        
        if self.__create_variations:
            '''
            es werden mehr als ein Netz von einer bestimmten Layeranzahl erzeugt:
            wenn die Layeranzahl Range zwischen 7 und 9 liegt, self.__create_variations = True ist und
            die Variable self.__number_of_variations = 4 ist werden 4 Netze mit 7 Layern und 4 Netze
            mit 8 Layern erzeugt. Diese können dann gegeneinander getestet werden und geben eine bessere
            Übersicht über eine gute Layeranzahl.
            '''
            min_layer = self.__layer_range[0]
            max_layer = self.__layer_range[1]
            if min_layer == max_layer:
                max_layer += 1
            for layer in range(min_layer, max_layer): 
                variation_counter = 0
                while variation_counter < self.__number_of_variations:
                    variation_counter +=1 
                    dropout_counter = 0
                    act_count = 0
                    specs_dict = {}
                    middle = layer//2
                    for l in range(layer):
                        layer_specs = []
                        if self.__random_activation:#random activation pick ist aktiviert
                            act = random.choice(self.__activations)
                            key = act+str(act_count)
                            act_count += 1
                            if dropout_counter == self.__dropout_number:
                                #es wurden schon ausreichend dropout layer erzeugt
                                l_ = random.choice([x for x in self.__layer_types if x not in ['dropout']])
                            else:
                                l_ = random.choice(self.__layer_types)
                                if l_ == 'dropout':
                                    dropout_counter +=1
                                    
                            if l == 0:
                                in_ = self.__input_start
                                if l_ == 'dropout':
                                    dropout_counter = dropout_counter-1
                                    l_ = 'linear'
                                range_start = self.__in_out_range[0]
                                range_end = self.__in_out_range[1]
                                out_ = random.randint(range_start, range_end)
                                layer_specs.append(l_)
                                layer_specs.append(in_)
                                layer_specs.append(out_)
                            else:
                                layer_before = specs_dict[list(specs_dict.keys())[-1]]
                                out_alt = specs_dict[list(specs_dict.keys())[-1]][2]
                                l_type = layer_before[0]
                                i_ltype = -2
                                while l_type == 'dropout':#überprüfen ob vorhergegangenes Layer ein dropout layer war
                                    #sobald das vorhergegangene nicht-dropoutlayer gefunden wurde, wird output größe übernommen
                                    layer_before = specs_dict[list(specs_dict.keys())[i_ltype]]
                                    l_type = layer_before[0]
                                    out_alt = specs_dict[list(specs_dict.keys())[i_ltype]][2]
                                    i_ltype = i_ltype -1
                                if l <= middle: #in der ertsen hälfte nimmt output zu
                                    in_ = out_alt
                                    range_start = out_alt
                                    range_end = self.__in_out_range[1]
                                    out_ = random.randint(range_start, range_end)
                                else:#in zweiter hälfte der layer nimmt output wieder ab
                                    in_ = out_alt
                                    range_start = self.__in_out_range[0]
                                    range_end = out_alt
                                    out_ = random.randint(range_start, range_end)
                                layer_specs.append(l_)
                                layer_specs.append(in_)
                                layer_specs.append(out_)
                            if l == layer-1:
                                l_ = 'linear'
                                layer_specs = [l_,in_,self.__output_last]
                                specs_dict['last'] = layer_specs#layer wird ohne activation gespeichert und als letztes Layer des NN gekennzeichnet
                                
                            elif l == 0:
                                specs_dict['first'] = layer_specs
                            else:
                                #if l_ == 'dropout':#keine activation function bei dropout layern
                                #    key = 'no_activation'+str(act_count)
                                if specs_dict[list(specs_dict.keys())[-1]][0] == 'dropout':# keine activation function bei layern direkt nach einem dropout layer
                                    key = 'no_activation'+str(act_count)
                                specs_dict[key] = layer_specs
                    key = random.randint(0,10000)
                    while key in list(self.model_specs_combinations.keys()):
                         key = random.randint(0,10000)
                    self.model_specs_combinations[key]= specs_dict   
                    print(specs_dict,'\n')
                
        else:
            min_layer = self.__layer_range[0]
            max_layer = self.__layer_range[1]
            if min_layer == max_layer:
                max_layer += 1
            for layer in range(min_layer, max_layer): 
                
                dropout_counter = 0
                act_count = 0
                specs_dict = {}
                middle = layer//2
                for l in range(layer):
                    layer_specs = []
                    if self.__random_activation:#random activation pick ist aktiviert
                        act = random.choice(self.__activations)
                        key = act+str(act_count)
                        act_count += 1
                        if dropout_counter == self.__dropout_number:
                            #es wurden schon ausreichend dropout layer erzeugt
                            l_ = random.choice([x for x in self.__layer_types if x not in ['dropout']])
                        else:
                            l_ = random.choice(self.__layer_types)
                            if l_ == 'dropout':
                                dropout_counter +=1
                                
                        if l == 0:
                            in_ = self.__input_start
                            if l_ == 'dropout':
                                dropout_counter = dropout_counter-1
                                l_ = 'linear'
                            range_start = self.__in_out_range[0]
                            range_end = self.__in_out_range[1]
                            out_ = random.randint(range_start, range_end)
                            layer_specs.append(l_)
                            layer_specs.append(in_)
                            layer_specs.append(out_)
                        else:
                            layer_before = specs_dict[list(specs_dict.keys())[-1]]
                            out_alt = specs_dict[list(specs_dict.keys())[-1]][2]
                            l_type = layer_before[0]
                            i_ltype = -2
                            while l_type == 'dropout':#überprüfen ob vorhergegangenes Layer ein dropout layer war
                                #sobald das vorhergegangene nicht-dropoutlayer gefunden wurde, wird output größe übernommen
                                layer_before = specs_dict[list(specs_dict.keys())[i_ltype]]
                                l_type = layer_before[0]
                                out_alt = specs_dict[list(specs_dict.keys())[i_ltype]][2]
                                i_ltype = i_ltype -1
                            if l <= middle: #in der ertsen hälfte nimmt output zu
                                in_ = out_alt
                                range_start = out_alt
                                range_end = self.__in_out_range[1]
                                out_ = random.randint(range_start, range_end)
                            else:#in zweiter hälfte der layer nimmt output wieder ab
                                in_ = out_alt
                                range_start = self.__in_out_range[0]
                                range_end = out_alt
                                out_ = random.randint(range_start, range_end)
                            layer_specs.append(l_)
                            layer_specs.append(in_)
                            layer_specs.append(out_)
                        #if l == layer-1:
                        #    l_ = 'linear'
                        #    layer_specs = [l_,in_,self.__output_last]
                        #    specs_dict['last'] = layer_specs#layer wird ohne activation gespeichert und als letztes Layer des NN gekennzeichnet
                            
                        #elif l == 0:
                        if l == 0:
                            specs_dict['first'] = layer_specs
                        else:
                            #if l_ == 'dropout':#keine activation function bei dropout layern
                            #    key = 'no_activation'+str(act_count)
                            if specs_dict[list(specs_dict.keys())[-1]][0] == 'dropout':# keine activation function bei layern direkt nach einem dropout layer
                                key = 'no_activation'+str(act_count)
                            specs_dict[key] = layer_specs
                key = random.randint(0,10000)
                while key in list(self.model_specs_combinations.keys()):
                     key = random.randint(0,10000)
                self.model_specs_combinations[key]= specs_dict   
                print(specs_dict)
            

In [32]:
l = HP_Layer_Optimizer(layer_range=(8,12),
                       max_epochs = 4,
                       input_start = 10,
                       activations = ['relu'], 
                       random_activation=True,
                       create_combinations=True, 
                       create_variations = True, 
                       cuda = False)
#l.model_specs_combinations = netze
l.train_data = train_T
l.test_data = dev_T
l.validate_combinations()
l.get_all_information()
opt_combination = l.opt_combination

{'first': ['linear', 10, 197], 'relu1': ['dropout', 197, 198], 'no_activation3': ['linear', 197, 200], 'relu3': ['linear', 200, 200], 'relu4': ['linear', 200, 200], 'relu5': ['linear', 200, 99], 'relu6': ['linear', 99, 46], 'last': ['linear', 46, 1]} 

{'first': ['linear', 10, 190], 'relu1': ['linear', 190, 191], 'relu2': ['dropout', 191, 199], 'no_activation4': ['linear', 191, 199], 'relu4': ['linear', 199, 199], 'relu5': ['linear', 199, 78], 'relu6': ['linear', 78, 41], 'last': ['linear', 41, 1]} 

{'first': ['linear', 10, 106], 'relu1': ['linear', 106, 181], 'relu2': ['dropout', 181, 182], 'no_activation4': ['linear', 181, 191], 'relu4': ['linear', 191, 193], 'relu5': ['linear', 193, 109], 'relu6': ['linear', 109, 106], 'last': ['linear', 106, 1]} 

{'first': ['linear', 10, 80], 'relu1': ['dropout', 80, 200], 'no_activation3': ['linear', 80, 186], 'relu3': ['linear', 186, 200], 'relu4': ['linear', 200, 200], 'relu5': ['linear', 200, 191], 'relu6': ['linear', 191, 34], 'last': ['line

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\nn\modules\loss.py:431: UserWarning: Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([1, 46])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)



Train Epoche: 1 [15/96 (16%)]	Loss: 251.793564
Train Epoche: 1 [16/96 (17%)]	Loss: 59.271942
Train Epoche: 1 [17/96 (18%)]	Loss: 561.504700
Train Epoche: 1 [18/96 (19%)]	Loss: 180.836792
Train Epoche: 1 [19/96 (20%)]	Loss: 269.095795
Train Epoche: 1 [20/96 (21%)]	Loss: 311.735443
Train Epoche: 1 [21/96 (22%)]	Loss: 376.505829
Train Epoche: 1 [22/96 (23%)]	Loss: 416.605713
Train Epoche: 1 [23/96 (24%)]	Loss: 331.997253
Train Epoche: 1 [24/96 (25%)]	Loss: 13.256045
Train Epoche: 1 [25/96 (26%)]	Loss: 20.566534
Train Epoche: 1 [26/96 (27%)]	Loss: 111.469757
Train Epoche: 1 [27/96 (28%)]	Loss: 6.895361
Train Epoche: 1 [28/96 (29%)]	Loss: 156.429535
Train Epoche: 1 [29/96 (30%)]	Loss: 181.951935
Train Epoche: 1 [30/96 (31%)]	Loss: 29.700342
Train Epoche: 1 [31/96 (32%)]	Loss: 70.873901
Train Epoche: 1 [32/96 (33%)]	Loss: 128.860672
Train Epoche: 1 [33/96 (34%)]	Loss: 88.679100
Train Epoche: 1 [34/96 (35%)]	Loss: 57.623058
Train Epoche: 1 [35/96 (36%)]	Loss: 40.819237
Train Epoche: 1 [36/96

Train Epoche: 1 [190/96 (198%)]	Loss: 4.033254
Train Epoche: 1 [191/96 (199%)]	Loss: 4.526495
Train Epoche: 1 [192/96 (200%)]	Loss: 30.216686
Train Epoche: 1 [193/96 (201%)]	Loss: 47.790363
Train Epoche: 1 [194/96 (202%)]	Loss: 72.731827
Train Epoche: 1 [195/96 (203%)]	Loss: 63.541206
Train Epoche: 1 [196/96 (204%)]	Loss: 95.948921
Train Epoche: 1 [197/96 (205%)]	Loss: 55.877155
Train Epoche: 1 [198/96 (206%)]	Loss: 3.400936
Train Epoche: 1 [199/96 (207%)]	Loss: 4.702667
Train Epoche: 1 [200/96 (208%)]	Loss: 22.860792
Train Epoche: 1 [201/96 (209%)]	Loss: 1.968423
Train Epoche: 1 [202/96 (210%)]	Loss: 16.541157
Train Epoche: 1 [203/96 (211%)]	Loss: 4.631349
Train Epoche: 1 [204/96 (212%)]	Loss: 4.612988
Train Epoche: 1 [205/96 (214%)]	Loss: 5.956400
Train Epoche: 1 [206/96 (215%)]	Loss: 14.702932
Train Epoche: 1 [207/96 (216%)]	Loss: 240.253357
Train Epoche: 1 [208/96 (217%)]	Loss: 2.732464
Train Epoche: 1 [209/96 (218%)]	Loss: 39.400173
Train Epoche: 1 [210/96 (219%)]	Loss: 5.957652
T

Train Epoche: 1 [374/96 (390%)]	Loss: 0.470541
Train Epoche: 1 [375/96 (391%)]	Loss: 55.249252
Train Epoche: 1 [376/96 (392%)]	Loss: 329.887512
Train Epoche: 1 [377/96 (393%)]	Loss: 1.107235
Train Epoche: 1 [378/96 (394%)]	Loss: 2.735569
Train Epoche: 1 [379/96 (395%)]	Loss: 68.224586
Train Epoche: 1 [380/96 (396%)]	Loss: 64.393028
Train Epoche: 1 [381/96 (397%)]	Loss: 238.909561
Train Epoche: 1 [382/96 (398%)]	Loss: 129.283081
Train Epoche: 1 [383/96 (399%)]	Loss: 77.154785
Train Epoche: 1 [384/96 (400%)]	Loss: 297.199646
Train Epoche: 1 [385/96 (401%)]	Loss: 237.534225
Train Epoche: 1 [386/96 (402%)]	Loss: 57.908092
Train Epoche: 1 [387/96 (403%)]	Loss: 59.623924
Train Epoche: 1 [388/96 (404%)]	Loss: 7.457486
Train Epoche: 1 [389/96 (405%)]	Loss: 41.756420
Train Epoche: 1 [390/96 (406%)]	Loss: 306.189209
Train Epoche: 1 [391/96 (407%)]	Loss: 15.832221
Train Epoche: 1 [392/96 (408%)]	Loss: 106.632004
Train Epoche: 1 [393/96 (409%)]	Loss: 80.907875
Train Epoche: 1 [394/96 (410%)]	Loss:

...

Train Epoche: 3 [1823/96 (1899%)]	Loss: 1.843162
Train Epoche: 3 [1824/96 (1900%)]	Loss: 44.698353
Train Epoche: 3 [1825/96 (1901%)]	Loss: 102.773659
Train Epoche: 3 [1826/96 (1902%)]	Loss: 2.028207
Train Epoche: 3 [1827/96 (1903%)]	Loss: 13.190435
Train Epoche: 3 [1828/96 (1904%)]	Loss: 0.786776
Train Epoche: 3 [1829/96 (1905%)]	Loss: 15.131680
Train Epoche: 3 [1830/96 (1906%)]	Loss: 3.497208
Train Epoche: 3 [1831/96 (1907%)]	Loss: 124.772202
Train Epoche: 3 [1832/96 (1908%)]	Loss: 109.574730
Train Epoche: 3 [1833/96 (1909%)]	Loss: 2.733649
Train Epoche: 3 [1834/96 (1910%)]	Loss: 0.484546
Train Epoche: 3 [1835/96 (1911%)]	Loss: 19.920763
Train Epoche: 3 [1836/96 (1912%)]	Loss: 4.968613
Train Epoche: 3 [1837/96 (1914%)]	Loss: 0.020519
Train Epoche: 3 [1838/96 (1915%)]	Loss: 3.348643
Train Epoche: 3 [1839/96 (1916%)]	Loss: 4.661775
Train Epoche: 3 [1840/96 (1917%)]	Loss: 33.517502
Train Epoche: 3 [1841/96 (1918%)]	Loss: 32.056297
Train Epoche: 3 [1842/96 (1919%)]	Loss: 71.132164
Train E

Train Epoche: 3 [2003/96 (2086%)]	Loss: 0.051143
Train Epoche: 3 [2004/96 (2088%)]	Loss: 0.157678
Train Epoche: 3 [2005/96 (2089%)]	Loss: 0.017471
Train Epoche: 3 [2006/96 (2090%)]	Loss: 27.376850
Train Epoche: 3 [2007/96 (2091%)]	Loss: 12.942472
Train Epoche: 3 [2008/96 (2092%)]	Loss: 1.802980
Train Epoche: 3 [2009/96 (2093%)]	Loss: 40.458874
Train Epoche: 3 [2010/96 (2094%)]	Loss: 0.717492
Train Epoche: 3 [2011/96 (2095%)]	Loss: 12.787950
Train Epoche: 3 [2012/96 (2096%)]	Loss: 5.648337
Train Epoche: 3 [2013/96 (2097%)]	Loss: 42.227211
Train Epoche: 3 [2014/96 (2098%)]	Loss: 5.521235
Train Epoche: 3 [2015/96 (2099%)]	Loss: 8.163052
Train Epoche: 3 [2016/96 (2100%)]	Loss: 10.968637
Train Epoche: 3 [2017/96 (2101%)]	Loss: 0.095341
Train Epoche: 3 [2018/96 (2102%)]	Loss: 12.883415
Train Epoche: 3 [2019/96 (2103%)]	Loss: 1.479672
Train Epoche: 3 [2020/96 (2104%)]	Loss: 2.495270
Train Epoche: 3 [2021/96 (2105%)]	Loss: 60.876675
Train Epoche: 3 [2022/96 (2106%)]	Loss: 24.352413
Train Epoch

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\

All Model Combinations with encoding:
 {4707: {'first': ['linear', 10, 197], 'relu1': ['dropout', 197, 198], 'no_activation3': ['linear', 197, 200], 'relu3': ['linear', 200, 200], 'relu4': ['linear', 200, 200], 'relu5': ['linear', 200, 99], 'relu6': ['linear', 99, 46], 'last': ['linear', 46, 1]}, 6449: {'first': ['linear', 10, 190], 'relu1': ['linear', 190, 191], 'relu2': ['dropout', 191, 199], 'no_activation4': ['linear', 191, 199], 'relu4': ['linear', 199, 199], 'relu5': ['linear', 199, 78], 'relu6': ['linear', 78, 41], 'last': ['linear', 41, 1]}, 3256: {'first': ['linear', 10, 106], 'relu1': ['linear', 106, 181], 'relu2': ['dropout', 181, 182], 'no_activation4': ['linear', 181, 191], 'relu4': ['linear', 191, 193], 'relu5': ['linear', 193, 109], 'relu6': ['linear', 109, 106], 'last': ['linear', 106, 1]}, 3189: {'first': ['linear', 10, 80], 'relu1': ['dropout', 80, 200], 'no_activation3': ['linear', 80, 186], 'relu3': ['linear', 186, 200], 'relu4': ['linear', 200, 200], 'relu5': ['lin

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


In [124]:
#opt_layer = HP_Layer_Optimizer(layer_range=(6,10),
#                               in_out_range = (30,200),
#                               random_activation=True,#randompick von activation function, momentan geht False nicht
#                               cuda = True,
#                               dropout_num = 1,#anzahl zu erzeugender dropoutlayer
#                               lr = 0.0001,#lernrate für adam optimizer
#                               max_epochs = 5,#anzahl der Trainingsepochen
#                               activations = ['relu'],#normalerweise relu, tanh, sigmoid --> auskommentieren wenn wieder default
#                              input_start = 10
#                              )
#opt_layer.train_data = train_T
#opt_layer.test_data = dev_T
##opt_layer.validate_combinations()
##opt_layer.get_all_information()
##opt_combination = opt_layer.opt_combination

In [33]:
class HP_Optimizer(object):
    
    def __init__(self, lr_range = (0.0001,0.0001), step_size = 0.0001, max_epochs = (2,2), opt = 'Adam', cuda = True, dynamic = False, dyn_combination = {}):
        
        self.__model = Netz()
        self.__lr = lr_range
        self.__epochs = max_epochs
        self.__optimizer = opt
        self.__steps = step_size
        self.__combination_results = {}
        self.__combination_overview = {}
        self.train_data = None
        self.test_data = None
        self.cuda = cuda
        self.opt_combination = {}
        self.__dynamic = dynamic
        self.__dyn_combination = dyn_combination
        
        
    def validate_combinations(self):
        
        specifics = {}
        if self.__optimizer == 'Adam':
            
            #definieren der range für die lernratenoptimierung
            '''
            
            IST HIER WAS KAPUTT?
            
            '''
            if isinstance(self.__lr, tuple):
                lr_s = self.__lr[0]
                lr_e = self.__lr[1]
                #wurde eine range für die anzahl der epochen übergeben?
                if self.__epochs[0] == self.__epochs[1]:
                    #hyperparamter epochenanzahl wird nicht optimiert
                    max_epoch = self.__epochs[0]
                    if lr_s == lr_e:
                        #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                        print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                        #setzen des optimizers als Adam und erzeugen des Modells
                        if self.__dynamic:
                            self.__model = NetzDynamic(self.__dyn_combination)
                        else:
                            self.__model = Netz()
                        optimizer = optim.Adam(self.__model.parameters(), lr = lr_s)
                        for epoch in range(1,max_epoch):
                            self.__train(epoch, optimizer)     
                        result = self.__test()
                        A = result.prediction.tolist()
                        y = result.target.tolist()
                        mae = MAE(A,y)
                        specifics = {}
                        specifics['lr'] = lr_s
                        specifics['epochen'] = max_epoch
                        key = random.randint(0,10000)
                        while key in list(self.__combination_results.keys()):
                             key = random.randint(0,10000)
                        self.__combination_results[key] = mae
                        self.__combination_overview[key] = specifics 
                    else:
                        for l in np.arange(lr_s,lr_e, self.__steps):
                            #setzen des optimizers als Adam und erzeugen des Modells
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = l)
                            #trainieren des modells
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)  
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = l
                            specifics['epochen'] = max_epoch
                            #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics
                else:
                    for max_epoch in range(self.__epochs[0], self.__epochs[1]):
                        #definieren der range für die lernratenoptimierung
                        lr_s = self.__lr[0]
                        lr_e = self.__lr[1]
                        #hyperparamter epochenanzahl wird nicht optimiert
                        if lr_s == lr_e:
                            #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                            #print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = lr_s)
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)       
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = lr_s
                            specifics['epochen'] = max_epoch
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)  
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics          
                        else:
                            for l in np.arange(lr_s,lr_e, self.__steps):
                                if self.__dynamic:
                                    self.__model = NetzDynamic(self.__dyn_combination)
                                else:
                                    self.__model = Netz()
                                optimizer = optim.Adam(self.__model.parameters(), lr = l)
                                #trainieren des modells
                                for epoch in range(1,max_epoch):
                                    self.__train(epoch, optimizer)  
                                result = self.__test()
                                A = result.prediction.tolist()
                                y = result.target.tolist()
                                mae = MAE(A,y)
                                specifics = {}
                                specifics['lr'] = l
                                specifics['epochen'] = max_epoch
                                #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                                key = random.randint(0,10000)
                                while key in list(self.__combination_results.keys()):
                                     key = random.randint(0,10000)
                                self.__combination_results[key] = mae
                                self.__combination_overview[key] = specifics
                #finden der besten kombination nach minimalstem Error (MAE)
                key_min = min(self.__combination_results.keys(), key=(lambda k: self.__combination_results[k]))
                best_combination = self.__combination_overview[key_min]
                best_combination['mae'] = self.__combination_results[key_min]
                self.opt_combination = best_combination
            elif isinstance(self.__lr, list):
                #wurde eine range für die anzahl der epochen übergeben?
                if self.__epochs[0] == self.__epochs[1]:
                    #hyperparamter epochenanzahl wird nicht optimiert
                    max_epoch = self.__epochs[0]
                    if len(self.__lr) ==1:
                        #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                        print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                        #setzen des optimizers als Adam und erzeugen des Modells
                        if self.__dynamic:
                            self.__model = NetzDynamic(self.__dyn_combination)
                        else:
                            self.__model = Netz()
                        optimizer = optim.Adam(self.__model.parameters(), lr = self.__lr[0])
                        for epoch in range(1,max_epoch):
                            self.__train(epoch, optimizer)     
                        result = self.__test()
                        A = result.prediction.tolist()
                        y = result.target.tolist()
                        mae = MAE(A,y)
                        specifics = {}
                        specifics['lr'] = self.__lr[0]
                        specifics['epochen'] = max_epoch
                        key = random.randint(0,10000)
                        while key in list(self.__combination_results.keys()):
                             key = random.randint(0,10000)
                        self.__combination_results[key] = mae
                        self.__combination_overview[key] = specifics 
                    else:
                        for l in self.__lr:
                            #setzen des optimizers als Adam und erzeugen des Modells
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = l)
                            #trainieren des modells
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)  
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = l
                            specifics['epochen'] = max_epoch
                            #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics
                else:
                    for max_epoch in range(self.__epochs[0], self.__epochs[1]):
                        #definieren der range für die lernratenoptimierung
                        lr_s = self.__lr[0]
                        lr_e = self.__lr[1]
                        #hyperparamter epochenanzahl wird nicht optimiert
                        if len(self.__lr) == 1:
                            #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                            #print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = self.__lr[0])
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)       
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = self.__lr[0]
                            specifics['epochen'] = max_epoch
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)  
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics          
                        else:
                            for l in self.__lr:
                                if self.__dynamic:
                                    self.__model = NetzDynamic(self.__dyn_combination)
                                else:
                                    self.__model = Netz()
                                optimizer = optim.Adam(self.__model.parameters(), lr = l)
                                #trainieren des modells
                                for epoch in range(1,max_epoch):
                                    self.__train(epoch, optimizer)  
                                result = self.__test()
                                A = result.prediction.tolist()
                                y = result.target.tolist()
                                mae = MAE(A,y)
                                specifics = {}
                                specifics['lr'] = l
                                specifics['epochen'] = max_epoch
                                #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                                key = random.randint(0,10000)
                                while key in list(self.__combination_results.keys()):
                                     key = random.randint(0,10000)
                                self.__combination_results[key] = mae
                                self.__combination_overview[key] = specifics
                #finden der besten kombination nach minimalstem Error (MAE)
                key_min = min(self.__combination_results.keys(), key=(lambda k: self.__combination_results[k]))
                best_combination = self.__combination_overview[key_min]
                best_combination['mae'] = self.__combination_results[key_min]
                self.opt_combination = best_combination
                
        else:
            raise ('No valid optimizer given! Try Adam for example!')
            
    def __train(self, epoch, optimizer):
        if self.cuda:
            self.__model.cuda()
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0).cuda()
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    optimizer.zero_grad()
                    out = self.__model(data)
                    #print("Out: ", out, out.size())
                    #print("Target: ", target, target.size())
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                        epoch, batch_id *len(data), len(self.train_data),
                    100. * batch_id / len(self.train_data), loss.item()))
                    batch_id +=1
        else:
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    #data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)#.cuda()
                    shape = target.size()[1]
                    target = target.resize(shape,1)#.cuda()
                    optimizer.zero_grad()
                    out = self.__model(data)
                    #print("Out: ", out, out.size())
                    #print("Target: ", target, target.size())
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    #print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                    #    epoch, batch_id *len(data), len(train_data),
                    #100. * batch_id / len(train_data), loss.item()))
                    batch_id +=1
                    
            
    def __test(self):
        total = 0
        count = 0
        result_dict = {}
        result = pd.DataFrame(columns = ['target','prediction'])
        help_dict = {}
        if self.cuda:
            self.__model.cuda()
            for key in self.test_data.keys():
                #print(key)
                help_dict = {}
                for data, target in self.test_data[key]:
                    self.__model.eval()
                    #files.listdir(path)
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    out = self.__model(data).cpu()
                    #print(out)
                    out = out.detach().numpy()
                    #out = np.round(out)
                    target = target.cpu()
                    target = target.detach().numpy()
                    #print(data)
                    #print(data["driverId"])
                    total += abs(out - target[0][0])
                    #print("current_position: ", data[0][0].item())
                    #print("Output: ", out)
                    #print("Target: ", target)
                    help_dict[target[0][0]] = out
                    #print("Difference: ", out - target)
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                
                result = result.append(t, sort = True)
                
        else:
            for raceId in self.test_data.keys():
                #print(key)
                help_dict = {}
                for data, target in self.test_data[raceId]:
                    self.__model.eval()
                    #files.listdir(path)
                    #data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1)#.cuda()
                    out = self.__model(data)#.cpu()
                    #print(out)
                    out = out.detach().numpy()
                    #out = np.round(out)
                    #target = target.cpu()
                    target = target.detach().numpy()
                    #print(data)
                    #print(data["driverId"])
                    total += abs(out - target[0][0])
                    #print("current_position: ", data[0][0].item())
                    #print("Output: ", out)
                    #print("Target: ", target)
                    help_dict[target[0][0]] = out
                    #print("Difference: ", out - target)
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                result = result.append(t, sort = True)
        return result
         
            
    def get_all_information(self):
        
        print('Chosen Model:',self.__model)
        print('Learningrate Range:',self.__lr)
        print('Maximum Epochs:', self.__epochs)
        print('Chosen Optimizer:', self.__optimizer)
        print('Result Encoding:', self.__combination_overview)
        print('Results:', self.__combination_results)
        print('Optimale Kombination:', self.opt_combination)
        
    def help(self):
        print('Parameters with defaults:\nlr_range --> (0.0001,0.0001),\nstep_size--> 0.0001,\nmax_epochs-->(2,2),\nopt-->"Adam",\ncuda=True')
        print('lr_range: Tupel with learnrate range')
        print('step_size: float/int for step_size of learnrate')
        print('max_epochs: Tupel with number of epochs range')
        print('opt: Optimizer (by default Adam)')
        print('cuda: True/False if cuda should be used, default = True\n')
        print('Attributes:')
        print('set self.train_data as dictionary with races (form: {raceId: race(dataframe)})')
        print('set self.test_data as dictionary with races (form: {raceId: race(dataframe)})')
        print('self.opt_combination: Dictionary which contains the best combination of the given parameters\n')
        print('Methods:')
        print('call self.validate_combination() to compare all combinations')
        print('get all information/results with self.get_all_information()')

Paralleles Aufrufen des Optimierers, übergeben der zuvor erzeugten Test- und Trainingsdatensätze, angeben der Intervalle für die die Hyperparameter getestet werden sollen (Lernrate und Epochenanzahl). Für das dynamische Modell wird das Dictionary übergeben, welches von dem Layer Optimizer am besten bewertet wurde. Der "normale" HP_Optimizer basiert auf der Klasse Netz().

In [36]:
h = HP_Optimizer(lr_range = [0.0002,0.00045],step_size = 0.0001, max_epochs=(3,5),cuda = False)
opt_={}
for key in opt_combination.keys():
    if key != 'mae':#mae wird noch in dictionary von HP_Optimizer hinzugefügt und muss entfernt werden
        opt_[key] = opt_combination[key]
h_dynamic = HP_Optimizer(lr_range = [0.0002,0.00045],step_size = 0.0001, max_epochs=(3,5),cuda = False, dynamic = True, dyn_combination = opt_)
#h_dynamic = HP_Optimizer(lr_range = [0.0002,0.00045],step_size = 0.0001, max_epochs=(3,5),cuda = False, dynamic = True, dyn_combination = julian)
h.help()
h.train_data = train_T
h_dynamic.train_data = train_T

h.test_data = dev_T
h_dynamic.test_data = dev_T

h.validate_combinations()
h_dynamic.validate_combinations()

h.get_all_information()
h_dynamic.get_all_information()

Parameters with defaults:
lr_range --> (0.0001,0.0001),
step_size--> 0.0001,
max_epochs-->(2,2),
opt-->"Adam",
cuda=True
lr_range: Tupel with learnrate range
step_size: float/int for step_size of learnrate
max_epochs: Tupel with number of epochs range
opt: Optimizer (by default Adam)
cuda: True/False if cuda should be used, default = True

Attributes:
set self.train_data as dictionary with races (form: {raceId: race(dataframe)})
set self.test_data as dictionary with races (form: {raceId: race(dataframe)})
self.opt_combination: Dictionary which contains the best combination of the given parameters

Methods:
call self.validate_combination() to compare all combinations
get all information/results with self.get_all_information()


c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\

Chosen Model: Netz(
  (fc1): Linear(in_features=10, out_features=150, bias=True)
  (fc2): Linear(in_features=150, out_features=180, bias=True)
  (fc3): Linear(in_features=180, out_features=190, bias=True)
  (fc4): Linear(in_features=190, out_features=120, bias=True)
  (fc5): Linear(in_features=120, out_features=100, bias=True)
  (fc6): Linear(in_features=100, out_features=70, bias=True)
  (fc7): Linear(in_features=70, out_features=30, bias=True)
  (fc8): Linear(in_features=30, out_features=1, bias=True)
  (dropout): Dropout(p=0.5, inplace=False)
)
Learningrate Range: [0.0002, 0.00045]
Maximum Epochs: (3, 5)
Chosen Optimizer: Adam
Result Encoding: {3181: {'lr': 0.0002, 'epochen': 3}, 7799: {'lr': 0.00045, 'epochen': 3}, 4487: {'lr': 0.0002, 'epochen': 4}, 1172: {'lr': 0.00045, 'epochen': 4, 'mae': 2.0482897384305834}}
Results: {3181: 2.193158953722334, 7799: 2.13682092555332, 4487: 2.2012072434607646, 1172: 2.0482897384305834}
Optimale Kombination: {'lr': 0.00045, 'epochen': 4, 'mae': 2

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


Es werden die als optimal in den gegebenen Intervallen genommenen Werte aus dem Optimierer genommen und ein neues Modell mit diesen Parametern trainiert. Zum Schluss werden die Ergebnisse des Testlaufes auf den Testdaten ausgegeben.
Dies geschieht genauso mit dem zuvor dynamisch erzeugten Modell. Diese können so direkt miteinander verglichen werden.

In [37]:
max_epochs = h.opt_combination['epochen']
max_epochs_dyn = h_dynamic.opt_combination['epochen']
lr = h.opt_combination['lr']
lr_dynamic = h_dynamic.opt_combination['lr']

#cuda = input('Cuda? [y/n]: ')
#opt_combination = julian
cuda = 'n'
model = Netz()
opt={}
for key in opt_combination.keys():
#for key in julian.keys():
    if key != 'mae':#mae wird noch in dictionary von HP_Optimizer hinzugefügt und muss entfernt werden
        opt[key] = opt_combination[key]
#model_dynamic = NetzDynamic(opt)
model_dynamic = NetzDynamic(julian)
if cuda.lower() == 'y':
    model.cuda() 
    model_dynamic.cuda()

    
optimizer = optim.Adam(model.parameters(), lr = lr)     
optimizer_d = optim.Adam(model_dynamic.parameters(), lr = lr_dynamic)   

def train_cuda(epoch):
    model.train()
    batch_id = 0
    for key in train_T.keys():
        
        for data, target in train_T[key]:
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0).cuda()
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            optimizer.zero_grad()
            out = model(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
        
    #random.shuffle(train_data)
def train_(epoch):
    model.train()
    batch_id = 0
    for key in train_T.keys():
        for data, target in train_T[key]:
            #data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)#.cuda()
            shape = target.size()[1]
            target = target.resize(shape,1)#.cuda()
            optimizer.zero_grad()
            out = model(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
            
def train_cuda_dynamic(epoch):
    model_dynamic.train()
    batch_id = 0
    for key in train_T.keys():
        
        for data, target in train_T[key]:
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0).cuda()
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            optimizer_d.zero_grad()
            out = model_dynamic(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer_d.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
        
    #random.shuffle(train_data)
def train_dynamic(epoch):
    model_dynamic.train()
    batch_id = 0
    for key in train_T.keys():
        for data, target in train_T[key]:
            #data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)#.cuda()
            shape = target.size()[1]
            target = target.resize(shape,1)#.cuda()
            optimizer_d.zero_grad()
            out = model_dynamic(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer_d.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
        
    #random.shuffle(train_data)
if cuda.lower() == 'y':
    for epoch in range(1,max_epochs):
        train_cuda(epoch) 
    for epoch in range(1,max_epochs_dyn):
        train_cuda_dynamic(epoch) 
else:
    for epoch in range(1,max_epochs):
        train_(epoch)  
    for epoch in range(1,max_epochs_dyn):
        train_dynamic(epoch)  
        

c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


Train Epoche: 1 [0/96 (0%)]	Loss: 4.198149
Train Epoche: 1 [1/96 (1%)]	Loss: 16.383038
Train Epoche: 1 [2/96 (2%)]	Loss: 145.149536
Train Epoche: 1 [3/96 (3%)]	Loss: 577.576782
Train Epoche: 1 [4/96 (4%)]	Loss: 577.369995
Train Epoche: 1 [5/96 (5%)]	Loss: 169.248795
Train Epoche: 1 [6/96 (6%)]	Loss: 81.437363
Train Epoche: 1 [7/96 (7%)]	Loss: 49.259041
Train Epoche: 1 [8/96 (8%)]	Loss: 25.034706
Train Epoche: 1 [9/96 (9%)]	Loss: 36.116791
Train Epoche: 1 [10/96 (10%)]	Loss: 120.624359
Train Epoche: 1 [11/96 (11%)]	Loss: 99.323128
Train Epoche: 1 [12/96 (12%)]	Loss: 8.872836
Train Epoche: 1 [13/96 (14%)]	Loss: 0.897069
Train Epoche: 1 [14/96 (15%)]	Loss: 222.535828
Train Epoche: 1 [15/96 (16%)]	Loss: 253.592789
Train Epoche: 1 [16/96 (17%)]	Loss: 60.839592
Train Epoche: 1 [17/96 (18%)]	Loss: 559.713989
Train Epoche: 1 [18/96 (19%)]	Loss: 184.436890
Train Epoche: 1 [19/96 (20%)]	Loss: 264.548950
Train Epoche: 1 [20/96 (21%)]	Loss: 308.028503
Train Epoche: 1 [21/96 (22%)]	Loss: 366.902374

Train Epoche: 1 [195/96 (203%)]	Loss: 116.825882
Train Epoche: 1 [196/96 (204%)]	Loss: 89.662209
Train Epoche: 1 [197/96 (205%)]	Loss: 15.128757
Train Epoche: 1 [198/96 (206%)]	Loss: 0.162075
Train Epoche: 1 [199/96 (207%)]	Loss: 1.509162
Train Epoche: 1 [200/96 (208%)]	Loss: 0.168394
Train Epoche: 1 [201/96 (209%)]	Loss: 0.877133
Train Epoche: 1 [202/96 (210%)]	Loss: 20.604872
Train Epoche: 1 [203/96 (211%)]	Loss: 20.948210
Train Epoche: 1 [204/96 (212%)]	Loss: 0.146577
Train Epoche: 1 [205/96 (214%)]	Loss: 14.528445
Train Epoche: 1 [206/96 (215%)]	Loss: 15.395657
Train Epoche: 1 [207/96 (216%)]	Loss: 163.222931
Train Epoche: 1 [208/96 (217%)]	Loss: 2.167217
Train Epoche: 1 [209/96 (218%)]	Loss: 9.743363
Train Epoche: 1 [210/96 (219%)]	Loss: 0.000692
Train Epoche: 1 [211/96 (220%)]	Loss: 38.523010
Train Epoche: 1 [212/96 (221%)]	Loss: 1.634432
Train Epoche: 1 [213/96 (222%)]	Loss: 9.091032
Train Epoche: 1 [214/96 (223%)]	Loss: 75.341095
Train Epoche: 1 [215/96 (224%)]	Loss: 40.787922


Train Epoche: 1 [380/96 (396%)]	Loss: 3.377506
Train Epoche: 1 [381/96 (397%)]	Loss: 151.367462
Train Epoche: 1 [382/96 (398%)]	Loss: 9.404824
Train Epoche: 1 [383/96 (399%)]	Loss: 56.097897
Train Epoche: 1 [384/96 (400%)]	Loss: 291.762360
Train Epoche: 1 [385/96 (401%)]	Loss: 16.813179
Train Epoche: 1 [386/96 (402%)]	Loss: 1.064844
Train Epoche: 1 [387/96 (403%)]	Loss: 16.034824
Train Epoche: 1 [388/96 (404%)]	Loss: 2.413909
Train Epoche: 1 [389/96 (405%)]	Loss: 33.248798
Train Epoche: 1 [390/96 (406%)]	Loss: 264.049347
Train Epoche: 1 [391/96 (407%)]	Loss: 8.014331
Train Epoche: 1 [392/96 (408%)]	Loss: 9.172546
Train Epoche: 1 [393/96 (409%)]	Loss: 9.888824
Train Epoche: 1 [394/96 (410%)]	Loss: 47.596401
Train Epoche: 1 [395/96 (411%)]	Loss: 39.308056
Train Epoche: 1 [396/96 (412%)]	Loss: 169.358307
Train Epoche: 1 [397/96 (414%)]	Loss: 26.525547
Train Epoche: 1 [398/96 (415%)]	Loss: 6.437129
Train Epoche: 1 [399/96 (416%)]	Loss: 6.752615
Train Epoche: 1 [400/96 (417%)]	Loss: 1.74485

Train Epoche: 1 [569/96 (593%)]	Loss: 38.882488
Train Epoche: 1 [570/96 (594%)]	Loss: 154.904343
Train Epoche: 1 [571/96 (595%)]	Loss: 94.064796
Train Epoche: 1 [572/96 (596%)]	Loss: 103.476448
Train Epoche: 1 [573/96 (597%)]	Loss: 6.246000
Train Epoche: 1 [574/96 (598%)]	Loss: 21.077066
Train Epoche: 1 [575/96 (599%)]	Loss: 7.238466
Train Epoche: 1 [576/96 (600%)]	Loss: 93.693268
Train Epoche: 1 [577/96 (601%)]	Loss: 5.943145
Train Epoche: 1 [578/96 (602%)]	Loss: 46.566082
Train Epoche: 1 [579/96 (603%)]	Loss: 69.989548
Train Epoche: 1 [580/96 (604%)]	Loss: 0.283819
Train Epoche: 1 [581/96 (605%)]	Loss: 5.241999
Train Epoche: 1 [582/96 (606%)]	Loss: 13.259692
Train Epoche: 1 [583/96 (607%)]	Loss: 84.791183
Train Epoche: 1 [584/96 (608%)]	Loss: 0.678466
Train Epoche: 1 [585/96 (609%)]	Loss: 20.656046
Train Epoche: 1 [586/96 (610%)]	Loss: 5.357956
Train Epoche: 1 [587/96 (611%)]	Loss: 4.642324
Train Epoche: 1 [588/96 (612%)]	Loss: 79.094910
Train Epoche: 1 [589/96 (614%)]	Loss: 81.62870

...

Train Epoche: 3 [1281/96 (1334%)]	Loss: 1.727912
Train Epoche: 3 [1282/96 (1335%)]	Loss: 0.013312
Train Epoche: 3 [1283/96 (1336%)]	Loss: 10.240637
Train Epoche: 3 [1284/96 (1338%)]	Loss: 18.815989
Train Epoche: 3 [1285/96 (1339%)]	Loss: 0.042682
Train Epoche: 3 [1286/96 (1340%)]	Loss: 0.941136
Train Epoche: 3 [1287/96 (1341%)]	Loss: 56.201401
Train Epoche: 3 [1288/96 (1342%)]	Loss: 23.803410
Train Epoche: 3 [1289/96 (1343%)]	Loss: 20.150139
Train Epoche: 3 [1290/96 (1344%)]	Loss: 8.879260
Train Epoche: 3 [1291/96 (1345%)]	Loss: 10.946609
Train Epoche: 3 [1292/96 (1346%)]	Loss: 4.452137
Train Epoche: 3 [1293/96 (1347%)]	Loss: 19.195004
Train Epoche: 3 [1294/96 (1348%)]	Loss: 2.510460
Train Epoche: 3 [1295/96 (1349%)]	Loss: 13.027058
Train Epoche: 3 [1296/96 (1350%)]	Loss: 0.107620
Train Epoche: 3 [1297/96 (1351%)]	Loss: 17.058704
Train Epoche: 3 [1298/96 (1352%)]	Loss: 6.723594
Train Epoche: 3 [1299/96 (1353%)]	Loss: 0.022177
Train Epoche: 3 [1300/96 (1354%)]	Loss: 0.590825
Train Epoch

Train Epoche: 3 [1460/96 (1521%)]	Loss: 4.306495
Train Epoche: 3 [1461/96 (1522%)]	Loss: 1.243617
Train Epoche: 3 [1462/96 (1523%)]	Loss: 29.600901
Train Epoche: 3 [1463/96 (1524%)]	Loss: 3.716233
Train Epoche: 3 [1464/96 (1525%)]	Loss: 1.626534
Train Epoche: 3 [1465/96 (1526%)]	Loss: 3.971897
Train Epoche: 3 [1466/96 (1527%)]	Loss: 2.704571
Train Epoche: 3 [1467/96 (1528%)]	Loss: 15.947484
Train Epoche: 3 [1468/96 (1529%)]	Loss: 39.073719
Train Epoche: 3 [1469/96 (1530%)]	Loss: 1.115401
Train Epoche: 3 [1470/96 (1531%)]	Loss: 0.767970
Train Epoche: 3 [1471/96 (1532%)]	Loss: 71.918839
Train Epoche: 3 [1472/96 (1533%)]	Loss: 63.713516
Train Epoche: 3 [1473/96 (1534%)]	Loss: 0.009940
Train Epoche: 3 [1474/96 (1535%)]	Loss: 2.750417
Train Epoche: 3 [1475/96 (1536%)]	Loss: 0.004343
Train Epoche: 3 [1476/96 (1538%)]	Loss: 0.034746
Train Epoche: 3 [1477/96 (1539%)]	Loss: 0.202490
Train Epoche: 3 [1478/96 (1540%)]	Loss: 2.427661
Train Epoche: 3 [1479/96 (1541%)]	Loss: 18.978374
Train Epoche: 

Train Epoche: 3 [1646/96 (1715%)]	Loss: 5.981403
Train Epoche: 3 [1647/96 (1716%)]	Loss: 0.566613
Train Epoche: 3 [1648/96 (1717%)]	Loss: 0.230913
Train Epoche: 3 [1649/96 (1718%)]	Loss: 53.656601
Train Epoche: 3 [1650/96 (1719%)]	Loss: 9.880095
Train Epoche: 3 [1651/96 (1720%)]	Loss: 2.522390
Train Epoche: 3 [1652/96 (1721%)]	Loss: 0.441526
Train Epoche: 3 [1653/96 (1722%)]	Loss: 0.309832
Train Epoche: 3 [1654/96 (1723%)]	Loss: 19.928354
Train Epoche: 3 [1655/96 (1724%)]	Loss: 91.549652
Train Epoche: 3 [1656/96 (1725%)]	Loss: 3.716460
Train Epoche: 3 [1657/96 (1726%)]	Loss: 0.315644
Train Epoche: 3 [1658/96 (1727%)]	Loss: 0.067659
Train Epoche: 3 [1659/96 (1728%)]	Loss: 250.059128
Train Epoche: 3 [1660/96 (1729%)]	Loss: 24.369650
Train Epoche: 3 [1661/96 (1730%)]	Loss: 7.603045
Train Epoche: 3 [1662/96 (1731%)]	Loss: 17.524599
Train Epoche: 3 [1663/96 (1732%)]	Loss: 0.521775
Train Epoche: 3 [1664/96 (1733%)]	Loss: 7.778944
Train Epoche: 3 [1665/96 (1734%)]	Loss: 40.368374
Train Epoche

Train Epoche: 3 [1831/96 (1907%)]	Loss: 109.630249
Train Epoche: 3 [1832/96 (1908%)]	Loss: 44.180016
Train Epoche: 3 [1833/96 (1909%)]	Loss: 0.002303
Train Epoche: 3 [1834/96 (1910%)]	Loss: 13.582110
Train Epoche: 3 [1835/96 (1911%)]	Loss: 20.280258
Train Epoche: 3 [1836/96 (1912%)]	Loss: 63.820774
Train Epoche: 3 [1837/96 (1914%)]	Loss: 0.101698
Train Epoche: 3 [1838/96 (1915%)]	Loss: 0.792075
Train Epoche: 3 [1839/96 (1916%)]	Loss: 3.654629
Train Epoche: 3 [1840/96 (1917%)]	Loss: 16.800226
Train Epoche: 3 [1841/96 (1918%)]	Loss: 9.397526
Train Epoche: 3 [1842/96 (1919%)]	Loss: 30.095432
Train Epoche: 3 [1843/96 (1920%)]	Loss: 33.186787
Train Epoche: 3 [1844/96 (1921%)]	Loss: 6.371819
Train Epoche: 3 [1845/96 (1922%)]	Loss: 3.741936
Train Epoche: 3 [1846/96 (1923%)]	Loss: 1.161274
Train Epoche: 3 [1847/96 (1924%)]	Loss: 0.523538
Train Epoche: 3 [1848/96 (1925%)]	Loss: 18.085724
Train Epoche: 3 [1849/96 (1926%)]	Loss: 0.763547
Train Epoche: 3 [1850/96 (1927%)]	Loss: 8.779410
Train Epoc

Train Epoche: 3 [2008/96 (2092%)]	Loss: 1.932647
Train Epoche: 3 [2009/96 (2093%)]	Loss: 2.768869
Train Epoche: 3 [2010/96 (2094%)]	Loss: 3.621459
Train Epoche: 3 [2011/96 (2095%)]	Loss: 15.190217
Train Epoche: 3 [2012/96 (2096%)]	Loss: 2.781318
Train Epoche: 3 [2013/96 (2097%)]	Loss: 19.378414
Train Epoche: 3 [2014/96 (2098%)]	Loss: 0.593247
Train Epoche: 3 [2015/96 (2099%)]	Loss: 7.045074
Train Epoche: 3 [2016/96 (2100%)]	Loss: 10.977519
Train Epoche: 3 [2017/96 (2101%)]	Loss: 0.082703
Train Epoche: 3 [2018/96 (2102%)]	Loss: 0.768771
Train Epoche: 3 [2019/96 (2103%)]	Loss: 0.012708
Train Epoche: 3 [2020/96 (2104%)]	Loss: 0.001758
Train Epoche: 3 [2021/96 (2105%)]	Loss: 0.801309
Train Epoche: 3 [2022/96 (2106%)]	Loss: 0.006807
Train Epoche: 3 [2023/96 (2107%)]	Loss: 0.442181
Train Epoche: 3 [2024/96 (2108%)]	Loss: 30.064991
Train Epoche: 3 [2025/96 (2109%)]	Loss: 18.032722
Train Epoche: 3 [2026/96 (2110%)]	Loss: 1.724359
Train Epoche: 3 [2027/96 (2111%)]	Loss: 0.700634
Train Epoche: 3

In [38]:
def test_times_cuda(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        #print(key)
        help_dict = {}
        for data, target in test_final[key]:
            model.eval()
            #files.listdir(path)
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            out = model(data).cpu()
            #print(out)
            out = out.detach().numpy()
            #out = np.round(out)
            target = target.cpu()
            target = target.detach().numpy()
            #print(data)
            #print(data["driverId"])
            total += abs(out - target[0][0])
            #print("current_position: ", data[0][0].item())
            #print("Output: ", out)
            #print("Target: ", target)
            help_dict[target[0][0]] = out
            #print("Difference: ", out - target)
            count+=1
        #help_dict = sorted(help_dict.items(), key=operator.itemgetter(1))
        result_dict[key] = help_dict
        
    return result_dict

def test_times(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        #print(key)
        help_dict = {}
        for data, target in test_final[key]:
            model.eval()
            #files.listdir(path)
            #data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1)#.cuda()
            out = model(data)#.cpu()
            #print(out)
            out = out.detach().numpy()
            #out = np.round(out)
            #target = target.cpu()
            target = target.detach().numpy()
            #print(data)
            #print(data["driverId"])
            total += abs(out - target[0][0])
            #print("current_position: ", data[0][0].item())
            #print("Output: ", out)
            #print("Target: ", target)
            help_dict[target[0][0]] = out
            #print("Difference: ", out - target)
            count+=1
        #help_dict = sorted(help_dict.items(), key=operator.itemgetter(1))
        result_dict[key] = help_dict
        
    return result_dict

def test_times_cuda_dynamic(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        #print(key)
        help_dict = {}
        for data, target in test_final[key]:
            model_dynamic.eval()
            #files.listdir(path)
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            out = model_dynamic(data).cpu()
            #print(out)
            out = out.detach().numpy()
            #out = np.round(out)
            target = target.cpu()
            target = target.detach().numpy()
            #print(data)
            #print(data["driverId"])
            total += abs(out - target[0][0])
            #print("current_position: ", data[0][0].item())
            #print("Output: ", out)
            #print("Target: ", target)
            help_dict[target[0][0]] = out
            #print("Difference: ", out - target)
            count+=1
        #help_dict = sorted(help_dict.items(), key=operator.itemgetter(1))
        result_dict[key] = help_dict
        
    return result_dict

def test_times_dynamic(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        #print(key)
        help_dict = {}
        for data, target in test_final[key]:
            model_dynamic.eval()
            #files.listdir(path)
            #data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1)#.cuda()
            out = model_dynamic(data)#.cpu()
            #print(out)
            out = out.detach().numpy()
            #out = np.round(out)
            #target = target.cpu()
            target = target.detach().numpy()
            #print(data)
            #print(data["driverId"])
            total += abs(out - target[0][0])
            #print("current_position: ", data[0][0].item())
            #print("Output: ", out)
            #print("Target: ", target)
            help_dict[target[0][0]] = out
            #print("Difference: ", out - target)
            count+=1
        #help_dict = sorted(help_dict.items(), key=operator.itemgetter(1))
        result_dict[key] = help_dict
        
    return result_dict


if cuda.lower() =='y':
    total_results = test_times_cuda(test_T)
    total_results_dynamic = test_times_cuda_dynamic(test_T)
else:
    total_results = test_times(test_T)
    total_results_dynamic = test_times_dynamic(test_T)


In [39]:
result_dfs = {}
for raceId, dict in total_results.items():    
    #Auswerten der Vorhersagen aus den Outputdaten des Modells
    A = [x[0][0] for x in list((dict.values()))]
    A_dyn = [x[0][0] for x in list((total_results_dynamic[raceId].values()))]
    y = list(dict.keys())
    y_dyn = list(total_results_dynamic[raceId].keys())
    t = pd.DataFrame(columns = ['target', 'prediction'])
    t_dyn = pd.DataFrame(columns = ['target', 'prediction'])
    t['target'] = y
    t['prediction'] = A
    t_dyn['target'] = y_dyn
    t_dyn['prediction'] = A_dyn
    #print("raceId", raceId)
    temp = split_by_race[raceId]
    #name = split_by_race[raceId].where()
    #sortieren des DataFrames nach den vorhergesagten Positionen, aufsteigend
    end = sqldf.sqldf('''select * from t order by prediction ASC''')
    end.reset_index(inplace = True)
    end_dyn = sqldf.sqldf('''select * from t_dyn order by prediction ASC''')
    end_dyn.reset_index(inplace = True)
    #Da DF nun nach prediction aufsteigend sortiert ist, kann veränderter Index als predictete Position gesetzt werden
    end.rename(columns = {'index': 'predicted_position'},inplace = True)
    end_dyn.rename(columns = {'index': 'predicted_position'},inplace = True)
    #zur Übersichtlichkeit wird nun der endgültige DF nach den richtigen Positionen (target) sortiert (aufsteigend)
    end = sqldf.sqldf('''select * from end order by target ASC''')
    end_dyn = sqldf.sqldf('''select * from end_dyn order by target ASC''')
    end['predicted_position'] = end['predicted_position']+1
    end_dyn['predicted_position'] = end_dyn['predicted_position']+1
    #pred_name = sqldf.sqldf("""select 
    #            distinct
    #            d.driver_fullname as name,
    #            t.predicted_position as pred,
    #            d.podium_position as target_position
    #            from 
    #            end t inner join temp d
    #            on t.predicted_position = d.podium_position""")
    end["driver_pred"] = 0
    end["driver_target"] = 0
    end_dyn["driver_pred"] = 0
    end_dyn["driver_target"] = 0
    for pos in temp.podium_position.unique():
        
        name = temp.where(temp.podium_position == pos).dropna(how = "all")
        #print(name)
        name_ = name["driver_fullname"][list(name.index)[0]]
        idx_target = end.where(end.target == pos).dropna(how = "all").index
        idx_pred = end.where(end.predicted_position == pos).dropna(how = "all").index
        end.loc[idx_target,"driver_target"] = name_
        end.loc[idx_pred,"driver_pred"] = name_
        
        idx_target = end_dyn.where(end_dyn.target == pos).dropna(how = "all").index
        idx_pred = end_dyn.where(end_dyn.predicted_position == pos).dropna(how = "all").index
        end_dyn.loc[idx_target,"driver_target"] = name_
        end_dyn.loc[idx_pred,"driver_pred"] = name_
        
    #umstellen der Spaltenreihenfolge
    '''end = end[['target', 'predicted_position', 'prediction',"driver_target", "driver_pred"]]
    end_dyn = end_dyn[['target', 'predicted_position', 'prediction',"driver_target", "driver_pred"]]'''
    end = end[['target', 'predicted_position', 'prediction']]
    end_dyn = end_dyn[['target', 'predicted_position', 'prediction']]
    result_dfs[raceId] = end
    r = str(raceId)+'_dynamic'
    result_dfs[r] = end_dyn

In [40]:
for key, value in result_dfs.items():
    print('RaceId:',key)
    print(value,'\n')

RaceId: 932
    target  predicted_position  prediction
0      1.0                   1    3.137197
1      2.0                   2    3.381554
2      3.0                   4    4.348359
3      4.0                   3    4.195504
4      5.0                   7    7.454622
5      6.0                   5    7.345081
6      7.0                   8    9.006643
7      8.0                  10    9.513072
8      9.0                   9    9.080461
9     10.0                   6    7.385728
10    11.0                  11   10.009148
11    12.0                  13   12.463290
12    13.0                  12   10.367570
13    14.0                  15   13.406047
14    15.0                  14   13.346841
15    16.0                  16   14.254119
16    17.0                  18   18.001017
17    20.0                  17   17.732960 

RaceId: 932_dynamic
    target  predicted_position  prediction
0      1.0                   1    3.540939
1      2.0                   2    3.873777
2      3.0          

In [26]:
model_dynamic

NetzDynamic(
  (layers): ModuleList(
    (0): Linear(in_features=10, out_features=150, bias=True)
    (1): Linear(in_features=150, out_features=180, bias=True)
    (2): Dropout(p=0.5, inplace=False)
    (3): Linear(in_features=180, out_features=190, bias=True)
    (4): Linear(in_features=190, out_features=120, bias=True)
    (5): Linear(in_features=120, out_features=100, bias=True)
    (6): Linear(in_features=100, out_features=70, bias=True)
    (7): Linear(in_features=70, out_features=30, bias=True)
    (8): Linear(in_features=30, out_features=1, bias=True)
  )
)

In [27]:
model

Netz(
  (fc1): Linear(in_features=10, out_features=150, bias=True)
  (fc2): Linear(in_features=150, out_features=180, bias=True)
  (fc3): Linear(in_features=180, out_features=190, bias=True)
  (fc4): Linear(in_features=190, out_features=120, bias=True)
  (fc5): Linear(in_features=120, out_features=100, bias=True)
  (fc6): Linear(in_features=100, out_features=70, bias=True)
  (fc7): Linear(in_features=70, out_features=30, bias=True)
  (fc8): Linear(in_features=30, out_features=1, bias=True)
  (dropout): Dropout(p=0.5, inplace=False)
)

### Anhang

nogo_columns_hannah_kacke = [#'grid',
                #'race_completion',
                'lap_position','circuitId','lap_number',
                'podium_position', 'raceId',
                'grandprix_name', 'driver_fullname',
               'constructor_name', 'total_laps',
               'status_clean', 'constructorId',
                'total_milliseconds', 'driverId'
               'lap_in_milliseconds','year', 'stop_binary','constructorId_1.0',
                 'constructorId_3.0',
                 'constructorId_4.0',
                 'constructorId_5.0',
                 'constructorId_6.0',
                 'constructorId_9.0',
                 'constructorId_10.0',
                 'constructorId_15.0',
                 'constructorId_131.0',
                 'constructorId_164.0',
                 'constructorId_166.0',
                 'constructorId_205.0',
                 'constructorId_206.0',
                 'constructorId_207.0',
                 'constructorId_208.0',
                 'constructorId_209.0',
                 'constructorId_210.0']

In [ ]:
#test_netz = {'relu1':['linear',53,150], 'relu2':['linear',150,180], 'relu3':['dropout', 180,100],'relu4':['linear',180,30],'relu5':['linear',30,1]}

model_dynamic = NetzDynamic(opt_combination)

optimizer = optim.Adam(model_dynamic.parameters(), lr = 0.001)     

def train_cuda(epoch):
    model.train()
    batch_id = 0
    for key in train_T.keys():
        
        for data, target in train_T[key]:
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0).cuda()
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            optimizer.zero_grad()
            out = model(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
        
    #random.shuffle(train_data)
def train_(epoch):
    model.train()
    batch_id = 0
    for key in train_T.keys():
        for data, target in train_T[key]:
            #data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)#.cuda()
            shape = target.size()[1]
            target = target.resize(shape,1)#.cuda()
            optimizer.zero_grad()
            out = model(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
        

for epoch in range(1,3):
    train_(epoch)  
        

In [26]:

#cuda = input('Cuda? [y/n]: ')
opt_combination = julian
cuda = 'n'
#model = Netz()
opt={}
for key in opt_combination.keys():
#for key in julian.keys():
    if key != 'mae':#mae wird noch in dictionary von HP_Optimizer hinzugefügt und muss entfernt werden
        opt[key] = opt_combination[key]
#model_dynamic = NetzDynamic(opt)
model_dynamic = NetzDynamic(opt)
if cuda.lower() == 'y':
    model.cuda() 
    model_dynamic.cuda()

    
#optimizer = optim.Adam(model.parameters(), lr = lr)     
optimizer_d = optim.Adam(model_dynamic.parameters(), lr = 0.0001)   


def train_cuda_dynamic(epoch):
    model_dynamic.train()
    batch_id = 0
    for key in train_T.keys():
        
        for data, target in train_T[key]:
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0).cuda()
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            optimizer_d.zero_grad()
            out = model_dynamic(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer_d.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
        
    #random.shuffle(train_data)
def train_dynamic(epoch):
    model_dynamic.train()
    batch_id = 0
    for key in train_T.keys():
        for data, target in train_T[key]:
            #data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)#.cuda()
            shape = target.size()[1]
            target = target.resize(shape,1)#.cuda()
            optimizer_d.zero_grad()
            out = model_dynamic(data)
            #print("Out: ", out, out.size())
            #print("Target: ", target, target.size())
            criterion = nn.MSELoss()
            loss = criterion(out, target)
            loss.backward()
            optimizer_d.step()
            print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                epoch, batch_id *len(data), len(train),
            100. * batch_id / len(train), loss.item()))
            batch_id +=1
        
    #random.shuffle(train_data)
if cuda.lower() == 'y':
    for epoch in range(1,max_epochs):
        train_cuda(epoch) 
    for epoch in range(1,max_epochs_dyn):
        train_cuda_dynamic(epoch) 
else:
    #for epoch in range(1,max_epochs):
    #    train_(epoch)  
    for epoch in range(1,4):
        train_dynamic(epoch)  
        

dictionary im netz {'first': ['linear', 10, 150], 'relu0': ['linear', 150, 180], 'relu1': ['dropout', 0, 0], 'no_activation0': ['linear', 180, 190], 'relu2': ['linear', 190, 120], 'relu3': ['linear', 120, 100], 'relu4': ['linear', 100, 70], 'relu5': ['linear', 70, 30], 'relu6': ['linear', 30, 1]}
value teil in __init__ ['linear', 10, 150]
value teil in __init__ ['linear', 150, 180]
value teil in __init__ ['dropout', 0, 0]
value teil in __init__ ['linear', 180, 190]
value teil in __init__ ['linear', 190, 120]
value teil in __init__ ['linear', 120, 100]
value teil in __init__ ['linear', 100, 70]
value teil in __init__ ['linear', 70, 30]
value teil in __init__ ['linear', 30, 1]
Train Epoche: 1 [0/96 (0%)]	Loss: 4.093736
Train Epoche: 1 [1/96 (1%)]	Loss: 16.088638
Train Epoche: 1 [2/96 (2%)]	Loss: 144.608444
Train Epoche: 1 [3/96 (3%)]	Loss: 578.659180
Train Epoche: 1 [4/96 (4%)]	Loss: 576.526184
Train Epoche: 1 [5/96 (5%)]	Loss: 168.753677
Train Epoche: 1 [6/96 (6%)]	Loss: 81.006096
Train

Train Epoche: 1 [161/96 (168%)]	Loss: 87.212837
Train Epoche: 1 [162/96 (169%)]	Loss: 269.768646
Train Epoche: 1 [163/96 (170%)]	Loss: 14.037427
Train Epoche: 1 [164/96 (171%)]	Loss: 71.316185
Train Epoche: 1 [165/96 (172%)]	Loss: 3.540407
Train Epoche: 1 [166/96 (173%)]	Loss: 0.959892
Train Epoche: 1 [167/96 (174%)]	Loss: 67.831947
Train Epoche: 1 [168/96 (175%)]	Loss: 14.856614
Train Epoche: 1 [169/96 (176%)]	Loss: 18.015526
Train Epoche: 1 [170/96 (177%)]	Loss: 26.699425
Train Epoche: 1 [171/96 (178%)]	Loss: 2.128830
Train Epoche: 1 [172/96 (179%)]	Loss: 27.531767
Train Epoche: 1 [173/96 (180%)]	Loss: 31.793018
Train Epoche: 1 [174/96 (181%)]	Loss: 17.762600
Train Epoche: 1 [175/96 (182%)]	Loss: 9.959337
Train Epoche: 1 [176/96 (183%)]	Loss: 0.162128
Train Epoche: 1 [177/96 (184%)]	Loss: 11.238482
Train Epoche: 1 [178/96 (185%)]	Loss: 54.125244
Train Epoche: 1 [179/96 (186%)]	Loss: 4.750796
Train Epoche: 1 [180/96 (188%)]	Loss: 0.583238
Train Epoche: 1 [181/96 (189%)]	Loss: 0.372010

Train Epoche: 1 [351/96 (366%)]	Loss: 8.878772
Train Epoche: 1 [352/96 (367%)]	Loss: 61.025307
Train Epoche: 1 [353/96 (368%)]	Loss: 32.773182
Train Epoche: 1 [354/96 (369%)]	Loss: 45.664471
Train Epoche: 1 [355/96 (370%)]	Loss: 4.845269
Train Epoche: 1 [356/96 (371%)]	Loss: 211.617615
Train Epoche: 1 [357/96 (372%)]	Loss: 0.014597
Train Epoche: 1 [358/96 (373%)]	Loss: 54.013451
Train Epoche: 1 [359/96 (374%)]	Loss: 62.995987
Train Epoche: 1 [360/96 (375%)]	Loss: 21.754787
Train Epoche: 1 [361/96 (376%)]	Loss: 22.722599
Train Epoche: 1 [362/96 (377%)]	Loss: 0.239811
Train Epoche: 1 [363/96 (378%)]	Loss: 8.111058
Train Epoche: 1 [364/96 (379%)]	Loss: 2.166071
Train Epoche: 1 [365/96 (380%)]	Loss: 2.307796
Train Epoche: 1 [366/96 (381%)]	Loss: 25.467775
Train Epoche: 1 [367/96 (382%)]	Loss: 19.738607
Train Epoche: 1 [368/96 (383%)]	Loss: 33.155293
Train Epoche: 1 [369/96 (384%)]	Loss: 112.982956
Train Epoche: 1 [370/96 (385%)]	Loss: 77.146500
Train Epoche: 1 [371/96 (386%)]	Loss: 9.03567

Train Epoche: 1 [539/96 (561%)]	Loss: 3.974718
Train Epoche: 1 [540/96 (562%)]	Loss: 52.119247
Train Epoche: 1 [541/96 (564%)]	Loss: 23.042995
Train Epoche: 1 [542/96 (565%)]	Loss: 276.827515
Train Epoche: 1 [543/96 (566%)]	Loss: 60.330826
Train Epoche: 1 [544/96 (567%)]	Loss: 34.126255
Train Epoche: 1 [545/96 (568%)]	Loss: 153.021240
Train Epoche: 1 [546/96 (569%)]	Loss: 4.907269
Train Epoche: 1 [547/96 (570%)]	Loss: 99.377441
Train Epoche: 1 [548/96 (571%)]	Loss: 34.050709
Train Epoche: 1 [549/96 (572%)]	Loss: 19.136412
Train Epoche: 1 [550/96 (573%)]	Loss: 0.519858
Train Epoche: 1 [551/96 (574%)]	Loss: 47.223438
Train Epoche: 1 [552/96 (575%)]	Loss: 5.534687
Train Epoche: 1 [553/96 (576%)]	Loss: 74.614655
Train Epoche: 1 [554/96 (577%)]	Loss: 2.281276
Train Epoche: 1 [555/96 (578%)]	Loss: 21.732615
Train Epoche: 1 [556/96 (579%)]	Loss: 157.140091
Train Epoche: 1 [557/96 (580%)]	Loss: 108.479538
Train Epoche: 1 [558/96 (581%)]	Loss: 5.874425
Train Epoche: 1 [559/96 (582%)]	Loss: 0.05

Train Epoche: 1 [727/96 (757%)]	Loss: 70.472092
Train Epoche: 1 [728/96 (758%)]	Loss: 41.911205
Train Epoche: 1 [729/96 (759%)]	Loss: 82.187584
Train Epoche: 1 [730/96 (760%)]	Loss: 62.082542
Train Epoche: 1 [731/96 (761%)]	Loss: 68.983215
Train Epoche: 1 [732/96 (762%)]	Loss: 69.702217
Train Epoche: 1 [733/96 (764%)]	Loss: 59.823788
Train Epoche: 1 [734/96 (765%)]	Loss: 85.637253
Train Epoche: 1 [735/96 (766%)]	Loss: 44.613537
Train Epoche: 1 [736/96 (767%)]	Loss: 25.723080
Train Epoche: 1 [737/96 (768%)]	Loss: 34.552063
Train Epoche: 1 [738/96 (769%)]	Loss: 3.234308
Train Epoche: 1 [739/96 (770%)]	Loss: 35.185368
Train Epoche: 1 [740/96 (771%)]	Loss: 0.055216
Train Epoche: 1 [741/96 (772%)]	Loss: 0.212158
Train Epoche: 1 [742/96 (773%)]	Loss: 22.418642
Train Epoche: 1 [743/96 (774%)]	Loss: 18.521666
Train Epoche: 1 [744/96 (775%)]	Loss: 1.141616
Train Epoche: 1 [745/96 (776%)]	Loss: 16.758375
Train Epoche: 1 [746/96 (777%)]	Loss: 199.008972
Train Epoche: 1 [747/96 (778%)]	Loss: 98.34

...

Train Epoche: 3 [1278/96 (1331%)]	Loss: 11.853848
Train Epoche: 3 [1279/96 (1332%)]	Loss: 17.564800
Train Epoche: 3 [1280/96 (1333%)]	Loss: 116.037323
Train Epoche: 3 [1281/96 (1334%)]	Loss: 16.458586
Train Epoche: 3 [1282/96 (1335%)]	Loss: 0.005886
Train Epoche: 3 [1283/96 (1336%)]	Loss: 15.179563
Train Epoche: 3 [1284/96 (1338%)]	Loss: 119.423592
Train Epoche: 3 [1285/96 (1339%)]	Loss: 1.101253
Train Epoche: 3 [1286/96 (1340%)]	Loss: 58.822872
Train Epoche: 3 [1287/96 (1341%)]	Loss: 39.060188
Train Epoche: 3 [1288/96 (1342%)]	Loss: 40.010788
Train Epoche: 3 [1289/96 (1343%)]	Loss: 57.318092
Train Epoche: 3 [1290/96 (1344%)]	Loss: 0.119925
Train Epoche: 3 [1291/96 (1345%)]	Loss: 2.885539
Train Epoche: 3 [1292/96 (1346%)]	Loss: 0.422631
Train Epoche: 3 [1293/96 (1347%)]	Loss: 0.009876
Train Epoche: 3 [1294/96 (1348%)]	Loss: 0.651558
Train Epoche: 3 [1295/96 (1349%)]	Loss: 0.002327
Train Epoche: 3 [1296/96 (1350%)]	Loss: 0.017178
Train Epoche: 3 [1297/96 (1351%)]	Loss: 17.032434
Train E

Train Epoche: 3 [1454/96 (1515%)]	Loss: 2.273729
Train Epoche: 3 [1455/96 (1516%)]	Loss: 0.232367
Train Epoche: 3 [1456/96 (1517%)]	Loss: 0.600854
Train Epoche: 3 [1457/96 (1518%)]	Loss: 3.901900
Train Epoche: 3 [1458/96 (1519%)]	Loss: 64.963928
Train Epoche: 3 [1459/96 (1520%)]	Loss: 1.925819
Train Epoche: 3 [1460/96 (1521%)]	Loss: 7.554444
Train Epoche: 3 [1461/96 (1522%)]	Loss: 0.319901
Train Epoche: 3 [1462/96 (1523%)]	Loss: 14.249650
Train Epoche: 3 [1463/96 (1524%)]	Loss: 0.650215
Train Epoche: 3 [1464/96 (1525%)]	Loss: 2.754525
Train Epoche: 3 [1465/96 (1526%)]	Loss: 0.434337
Train Epoche: 3 [1466/96 (1527%)]	Loss: 14.723432
Train Epoche: 3 [1467/96 (1528%)]	Loss: 36.397583
Train Epoche: 3 [1468/96 (1529%)]	Loss: 11.743320
Train Epoche: 3 [1469/96 (1530%)]	Loss: 6.629126
Train Epoche: 3 [1470/96 (1531%)]	Loss: 2.309677
Train Epoche: 3 [1471/96 (1532%)]	Loss: 47.284325
Train Epoche: 3 [1472/96 (1533%)]	Loss: 3.006661
Train Epoche: 3 [1473/96 (1534%)]	Loss: 0.000411
Train Epoche: 

Train Epoche: 3 [1620/96 (1688%)]	Loss: 11.713249
Train Epoche: 3 [1621/96 (1689%)]	Loss: 19.518402
Train Epoche: 3 [1622/96 (1690%)]	Loss: 276.238251
Train Epoche: 3 [1623/96 (1691%)]	Loss: 8.784316
Train Epoche: 3 [1624/96 (1692%)]	Loss: 0.296548
Train Epoche: 3 [1625/96 (1693%)]	Loss: 16.323980
Train Epoche: 3 [1626/96 (1694%)]	Loss: 1.052885
Train Epoche: 3 [1627/96 (1695%)]	Loss: 13.325449
Train Epoche: 3 [1628/96 (1696%)]	Loss: 7.803781
Train Epoche: 3 [1629/96 (1697%)]	Loss: 7.123503
Train Epoche: 3 [1630/96 (1698%)]	Loss: 0.404304
Train Epoche: 3 [1631/96 (1699%)]	Loss: 0.777706
Train Epoche: 3 [1632/96 (1700%)]	Loss: 7.541173
Train Epoche: 3 [1633/96 (1701%)]	Loss: 29.620319
Train Epoche: 3 [1634/96 (1702%)]	Loss: 269.520264
Train Epoche: 3 [1635/96 (1703%)]	Loss: 15.218441
Train Epoche: 3 [1636/96 (1704%)]	Loss: 121.579430
Train Epoche: 3 [1637/96 (1705%)]	Loss: 2.115904
Train Epoche: 3 [1638/96 (1706%)]	Loss: 1.126320
Train Epoche: 3 [1639/96 (1707%)]	Loss: 36.749271
Train E

Train Epoche: 3 [1798/96 (1873%)]	Loss: 160.716248
Train Epoche: 3 [1799/96 (1874%)]	Loss: 12.703075
Train Epoche: 3 [1800/96 (1875%)]	Loss: 0.674810
Train Epoche: 3 [1801/96 (1876%)]	Loss: 10.293196
Train Epoche: 3 [1802/96 (1877%)]	Loss: 15.020954
Train Epoche: 3 [1803/96 (1878%)]	Loss: 8.324443
Train Epoche: 3 [1804/96 (1879%)]	Loss: 0.604784
Train Epoche: 3 [1805/96 (1880%)]	Loss: 1.390113
Train Epoche: 3 [1806/96 (1881%)]	Loss: 10.220760
Train Epoche: 3 [1807/96 (1882%)]	Loss: 5.584651
Train Epoche: 3 [1808/96 (1883%)]	Loss: 18.057880
Train Epoche: 3 [1809/96 (1884%)]	Loss: 0.123181
Train Epoche: 3 [1810/96 (1885%)]	Loss: 11.480764
Train Epoche: 3 [1811/96 (1886%)]	Loss: 2.633425
Train Epoche: 3 [1812/96 (1888%)]	Loss: 12.205793
Train Epoche: 3 [1813/96 (1889%)]	Loss: 119.190254
Train Epoche: 3 [1814/96 (1890%)]	Loss: 0.871736
Train Epoche: 3 [1815/96 (1891%)]	Loss: 6.996567
Train Epoche: 3 [1816/96 (1892%)]	Loss: 4.262865
Train Epoche: 3 [1817/96 (1893%)]	Loss: 0.925121
Train Epo

Train Epoche: 3 [1979/96 (2061%)]	Loss: 2.049289
Train Epoche: 3 [1980/96 (2062%)]	Loss: 0.025762
Train Epoche: 3 [1981/96 (2064%)]	Loss: 28.381071
Train Epoche: 3 [1982/96 (2065%)]	Loss: 0.480633
Train Epoche: 3 [1983/96 (2066%)]	Loss: 0.858763
Train Epoche: 3 [1984/96 (2067%)]	Loss: 0.541183
Train Epoche: 3 [1985/96 (2068%)]	Loss: 7.280099
Train Epoche: 3 [1986/96 (2069%)]	Loss: 0.115872
Train Epoche: 3 [1987/96 (2070%)]	Loss: 3.515954
Train Epoche: 3 [1988/96 (2071%)]	Loss: 0.050598
Train Epoche: 3 [1989/96 (2072%)]	Loss: 7.078212
Train Epoche: 3 [1990/96 (2073%)]	Loss: 44.254539
Train Epoche: 3 [1991/96 (2074%)]	Loss: 1.136256
Train Epoche: 3 [1992/96 (2075%)]	Loss: 3.898734
Train Epoche: 3 [1993/96 (2076%)]	Loss: 1.200093
Train Epoche: 3 [1994/96 (2077%)]	Loss: 0.990706
Train Epoche: 3 [1995/96 (2078%)]	Loss: 0.770464
Train Epoche: 3 [1996/96 (2079%)]	Loss: 2.541032
Train Epoche: 3 [1997/96 (2080%)]	Loss: 16.062889
Train Epoche: 3 [1998/96 (2081%)]	Loss: 3.095013
Train Epoche: 3 [

In [27]:
def test_times_cuda_dynamic(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        #print(key)
        help_dict = {}
        for data, target in test_final[key]:
            model_dynamic.eval()
            #files.listdir(path)
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            out = model_dynamic(data).cpu()
            #print(out)
            out = out.detach().numpy()
            #out = np.round(out)
            target = target.cpu()
            target = target.detach().numpy()
            #print(data)
            #print(data["driverId"])
            total += abs(out - target[0][0])
            #print("current_position: ", data[0][0].item())
            #print("Output: ", out)
            #print("Target: ", target)
            help_dict[target[0][0]] = out
            #print("Difference: ", out - target)
            count+=1
        #help_dict = sorted(help_dict.items(), key=operator.itemgetter(1))
        result_dict[key] = help_dict
        
    return result_dict

def test_times_dynamic(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        #print(key)
        help_dict = {}
        for data, target in test_final[key]:
            model_dynamic.eval()
            #files.listdir(path)
            #data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1)#.cuda()
            out = model_dynamic(data)#.cpu()
            #print(out)
            out = out.detach().numpy()
            #out = np.round(out)
            #target = target.cpu()
            target = target.detach().numpy()
            #print(data)
            #print(data["driverId"])
            total += abs(out - target[0][0])
            #print("current_position: ", data[0][0].item())
            #print("Output: ", out)
            #print("Target: ", target)
            help_dict[target[0][0]] = out
            #print("Difference: ", out - target)
            count+=1
        #help_dict = sorted(help_dict.items(), key=operator.itemgetter(1))
        result_dict[key] = help_dict
        
    return result_dict


if cuda.lower() =='y':
    #total_results = test_times_cuda(test_T)
    total_results_dynamic = test_times_cuda_dynamic(test_T)
else:
    #total_results = test_times(test_T)
    total_results_dynamic = test_times_dynamic(test_T)


In [28]:
result_dfs = {}
for raceId, dict in total_results_dynamic.items():    
    #Auswerten der Vorhersagen aus den Outputdaten des Modells
    #A = [x[0][0] for x in list((dict.values()))]
    A_dyn = [x[0][0] for x in list((total_results_dynamic[raceId].values()))]
    #y = list(dict.keys())
    y_dyn = list(total_results_dynamic[raceId].keys())
    #t = pd.DataFrame(columns = ['target', 'prediction'])
    t_dyn = pd.DataFrame(columns = ['target', 'prediction'])
    #t['target'] = y
    #t['prediction'] = A
    t_dyn['target'] = y_dyn
    t_dyn['prediction'] = A_dyn
    #print("raceId", raceId)
    temp = split_by_race[raceId]
    #name = split_by_race[raceId].where()
    #sortieren des DataFrames nach den vorhergesagten Positionen, aufsteigend
    #end = sqldf.sqldf('''select * from t order by prediction ASC''')
    #end.reset_index(inplace = True)
    end_dyn = sqldf.sqldf('''select * from t_dyn order by prediction ASC''')
    end_dyn.reset_index(inplace = True)
    #Da DF nun nach prediction aufsteigend sortiert ist, kann veränderter Index als predictete Position gesetzt werden
    #end.rename(columns = {'index': 'predicted_position'},inplace = True)
    end_dyn.rename(columns = {'index': 'predicted_position'},inplace = True)
    #zur Übersichtlichkeit wird nun der endgültige DF nach den richtigen Positionen (target) sortiert (aufsteigend)
    #end = sqldf.sqldf('''select * from end order by target ASC''')
    end_dyn = sqldf.sqldf('''select * from end_dyn order by target ASC''')
    #end['predicted_position'] = end['predicted_position']+1
    end_dyn['predicted_position'] = end_dyn['predicted_position']+1
    #pred_name = sqldf.sqldf("""select 
    #            distinct
    #            d.driver_fullname as name,
    #            t.predicted_position as pred,
    #            d.podium_position as target_position
    #            from 
    #            end t inner join temp d
    #            on t.predicted_position = d.podium_position""")
    #end["driver_pred"] = 0
    #end["driver_target"] = 0
    end_dyn["driver_pred"] = 0
    end_dyn["driver_target"] = 0
    for pos in temp.podium_position.unique():
        
        name = temp.where(temp.podium_position == pos).dropna(how = "all")
        #print(name)
        name_ = name["driver_fullname"][list(name.index)[0]]
        #idx_target = end_dyn.where(end_dyn.target == pos).dropna(how = "all").index
        #idx_pred = end_dyn.where(end_dyn.predicted_position == pos).dropna(how = "all").index
        #end.loc[idx_target,"driver_target"] = name_
        #end.loc[idx_pred,"driver_pred"] = name_
        
        idx_target = end_dyn.where(end_dyn.target == pos).dropna(how = "all").index
        idx_pred = end_dyn.where(end_dyn.predicted_position == pos).dropna(how = "all").index
        end_dyn.loc[idx_target,"driver_target"] = name_
        end_dyn.loc[idx_pred,"driver_pred"] = name_
        
    #umstellen der Spaltenreihenfolge
    '''end = end[['target', 'predicted_position', 'prediction',"driver_target", "driver_pred"]]
    end_dyn = end_dyn[['target', 'predicted_position', 'prediction',"driver_target", "driver_pred"]]'''
    #end = end[['target', 'predicted_position', 'prediction']]
    end_dyn = end_dyn[['target', 'predicted_position', 'prediction']]
    #result_dfs[raceId] = end
    r = str(raceId)+'_dynamic'
    result_dfs[r] = end_dyn

In [29]:
for key, value in result_dfs.items():
    print('RaceId:',key)
    print(value,'\n')

RaceId: 932_dynamic
    target  predicted_position  prediction
0      1.0                   1    2.952533
1      2.0                   2    3.169026
2      3.0                   4    3.814827
3      4.0                   3    3.354088
4      5.0                   5    7.343116
5      6.0                   6    7.372309
6      7.0                  12    9.212018
7      8.0                   9    8.537188
8      9.0                   8    8.009503
9     10.0                   7    7.657489
10    11.0                  10    9.017392
11    12.0                  13   11.405936
12    13.0                  11    9.095736
13    14.0                  14   12.029590
14    15.0                  16   13.036193
15    16.0                  15   12.833135
16    17.0                  18   15.789344
17    20.0                  17   15.622746 

RaceId: 943_dynamic
    target  predicted_position  prediction
0      1.0                   1    2.894784
1      2.0                   2    3.129318
2      3.0  

In [9]:
class NetzDynamic_falsch(nn.Module):
    
    def __init__(self, layer_information):
        super(NetzDynamic,self).__init__()
        self.__layer_information = layer_information
        #definieren von einer Moduleliste, die die Layer enthalten wird
        self.layers = nn.ModuleList()
        
        #erzeugen der in layer_information übergebeben Layer und hinzufügen zu layers Moduleliste
        for specs in self.__layer_information.values():
            type_ = specs[0]
            in_ = specs[1]
            out_ = specs[2]
            if type_ == 'linear':
                self.layers.append(nn.Linear(in_,out_))
            if type_ == 'dropout':
                self.layers.append(nn.Dropout())
        
    def forward(self, x):
        #definieren eines dynamischen forward pass, activation function richtet sich nach dictionary key
        lay_idx = 0
        for activation, specs in self.__layer_information.items():
            
            if activation.startswith('relu'):
                layer = self.layers[lay_idx] #auswählen des relevanten Layers aus layers ModuleList
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float())
                    x = F.relu(x.float())
            if activation.startswith('sigmoid'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float())
                    x = torch.sigmoid(x.float())
            if activation.startswith('tanh'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float())
                    x = torch.tanh(x.float())
            if activation.startswith('last'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float()) 
            if activation.startswith("first"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float())
            if activation.startswith("no_activation"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float()) 
            lay_idx += 1
        
        return x

Ansatz mit Julian: 

In [117]:
dropout = 1
drop_layer = 3
start_val = 10
out_val = 1
activations = ["relu", "sigmoid", "tanh"]
neuron_count = (30,200)
variations = 4
all_netz = []
x = 0
for layer in range(7,11):
    c = 0
    while c < variations:
        netz = {}
        for l in range(layer):
            x+=1
            specs_list = []
            if l == 0:
                in_ = start_val
                out_ = random.randint(neuron_count[0],neuron_count[1])
                key = "first"
                layer_type = "linear"
                specs_list.append(layer_type)
                specs_list.append(in_)
                specs_list.append(out_)
            elif l == drop_layer-1:
                key = "no_activation"+str(x)
                layer_type = "dropout"
                layer_before = netz[list(netz.keys())[l-2]]
                out_ = netz[list(netz.keys())[l-2]][2]
                specs_list.append(layer_type)
                specs_list.append(in_)
                specs_list.append(out_)
            elif l == drop_layer:
                key = "no_activation"+str(x)
                layer_type = "linear"
                layer_before = netz[list(netz.keys())[l-2]]
                in_ = netz[list(netz.keys())[l-2]][2]
                out_ = random.randint(neuron_count[0],neuron_count[1])
                specs_list.append(layer_type)
                specs_list.append(in_)
                specs_list.append(out_)
            elif l == layer -1:
                in_ = netz[list(netz.keys())[l-1]][2]
                out_ = out_val
                key = "last"
                layer_type = "linear"
                specs_list.append(layer_type)
                specs_list.append(in_)
                specs_list.append(out_)
            else:
                key = "relu"+str(x)
                layer_type = "linear"
                layer_before = netz[list(netz.keys())[l-1]]
                in_ = netz[list(netz.keys())[l-1]][2]
                out_ = random.randint(neuron_count[0],neuron_count[1])
                specs_list.append(layer_type)
                specs_list.append(in_)
                specs_list.append(out_)
                
            netz[key]=specs_list   
        all_netz.append(netz)
        c += 1

In [118]:
#netze werden kopiert, nur die activation functions werden verändert
temp_alle_netze = []
for netz in all_netz:
    x = 0
    for activation in ["sigmoid", "tanh"]:
        netz_ = {}
        for acts, layer_specs in netz.items():
            if acts in ["first", "last"] or acts.startswith("no_activation"):
                netz_[acts] = layer_specs
            else:
                key = activation+str(x)
                netz_[key] = layer_specs
                x +=1
        temp_alle_netze.append(netz_)
all_netz = all_netz+temp_alle_netze

In [43]:
netze = {}
infos = []
max_epochs = 6
r = 0
for instruction in all_netz:
    #Netz_D = NetzDynamic(instruction)
    k = str(len(instruction.keys()))+'_l_'+list(instruction.keys())[1]+str(r)
    r+=1
    #print(k)
    netze[k] = instruction